# Amazon Best Sellers

# Import Libraries

In [1]:
from bs4 import BeautifulSoup
import requests
import pandas as pd
import numpy as np
import re
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings("ignore")
import seaborn as sns 
# this statement allows the visuals to render within your Jupyter Notebook
%matplotlib inline 
# You can configure the format of the images: ‘png’, ‘retina’, ‘jpeg’, ‘svg’, ‘pdf’.
%config InlineBackend.figure_format = 'png'

In [2]:
# Project for best sales in amazon.sa

# Best Sellers in Electronics (Page 1)

In [3]:
header = {'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/96.0.4664.45 Safari/537.36'}
url = "https://www.amazon.sa/-/en/gp/bestsellers/electronics/?ie=UTF8&ref_=sv_sv_elec_all_1"

In [4]:
response = requests.get(url, {'headers':header})
response.status_code

200

In [5]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

# BeautifulSoup Basics

In [6]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [7]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [8]:
soup.find_all('li', {'class':'zg-item-immersion'})[0].find_all('a')[1].text

'\n3.0 out of 5 stars\n'

In [9]:
# create function to clean data 

In [10]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [11]:
#Test with the first electroni product to ensure functions are working
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))


SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB, 4GB RAM, LTE, Black (KSA Version)
3.0 out of 5 stars
3.0
2
2
SAR 539.00
539.00


In [12]:
soup.find_all("li", class_ = "zg-item-immersion")[3] 

<li class="zg-item-immersion" role="gridcell"><span class="a-list-item"><div class="a-section a-spacing-none aok-relative"><div class="a-row a-spacing-none aok-inline-block"><span class="a-size-small aok-float-left zg-badge-body zg-badge-color"><span class="zg-badge-text">#4</span></span><span class="aok-float-left zg-badge-triangle zg-badge-color"></span></div><span class="aok-inline-block zg-item"><a class="a-link-normal" href="/-/en/SAMSUNG-Galaxy-M12-Dual-Smartphone/dp/B08XY5X3J7?_encoding=UTF8&amp;psc=1"><span class="zg-text-center-align"><div class="a-section a-spacing-small"><img alt="SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB, 4GB RAM, 4G LTE, Black (KSA Version)" height="200" src="https://images-na.ssl-images-amazon.com/images/I/81DCMeVrbKS._AC_UL200_SR200,200_.jpg" width="200"/></div></span>
<div aria-hidden="true" class="p13n-sc-truncate p13n-sc-line-clamp-2" data-rows="2">
            SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB, 4GB RAM, 4G LTE, Black (KSA Version)
   

In [13]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

    

In [14]:
products_list

[{'pro_name': 'SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB, 4GB RAM, LTE, Black (KSA Version)',
  'pro_rate': '3.0 out of 5 stars',
  'pro_rate_clean': '3.0',
  'review_num': '2',
  'review_num_clean': '2',
  'pro_price': 'SAR 539.00',
  'pro_price_clean': '539.00'},
 {'pro_name': 'Samsung Galaxy A12 LTE Dual SIM Smartphone - 64GB Storage, 4GB RAM, Blue (KSA Version)',
  'pro_rate': '1.0 out of 5 stars',
  'pro_rate_clean': '1.0',
  'review_num': '2',
  'review_num_clean': '2',
  'pro_price': 'SAR 539.00',
  'pro_price_clean': '539.00'},
 {'pro_name': 'Apple 20W USB-C Power Adapter, White',
  'pro_rate': '4.5 out of 5 stars',
  'pro_rate_clean': '4.5',
  'review_num': '359',
  'review_num_clean': '359',
  'pro_price': 'SAR 79.00',
  'pro_price_clean': '79.00'},
 {'pro_name': 'SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB, 4GB RAM, 4G LTE, Black (KSA Version)',
  'pro_rate': '4.1 out of 5 stars',
  'pro_rate_clean': '4.1',
  'review_num': '40',
  'review_num_clean': '40',
  'pro_price

In [15]:
products_df1 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df1

pro_name            pro_rate  \
0   SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB,...  3.0 out of 5 stars   
1   Samsung Galaxy A12 LTE Dual SIM Smartphone - 6...  1.0 out of 5 stars   
2                Apple 20W USB-C Power Adapter, White  4.5 out of 5 stars   
3   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.1 out of 5 stars   
4                    Apple AirPods with Charging Case  4.1 out of 5 stars   
5   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.5 out of 5 stars   
6   Anker PowerCore Select 20000, 20000mAh Power B...  4.1 out of 5 stars   
7   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.2 out of 5 stars   
8   Apple Watch Series 6 (GPS, 44mm) - Space Grey ...  4.6 out of 5 stars   
9                               New Apple Airpods Pro  4.3 out of 5 stars   
10  Apple iPhone 12 Pro With FaceTime (256GB) - Pa...  4.2 out of 5 stars   
11  JBL Flip 5 Portable Speaker Waterproof Wireles...  4.6 out of 5 stars   
12  Anker Alkaline AAA Batteries (8-Pack), Long-La...  4.6 out of 5 stars   
13  Sony WH-1000XM4 Wireless Noise Cancelling Blue...  4.4 out of 5 stars   
14  EZVIZ C6N Pan/Tilt Camera FHD Indoor,1080p WiF...  4.2 out of 5 stars   
15  Stylus Pen for iPad with Palm Rejection, Activ...  3.4 out of 5 stars   
16  Apple iPhone 12 Pro With FaceTime (128GB) - Pa...  4.2 out of 5 stars   
17  Anker Alkaline AA Batteries (8-Pack), Long-Las...  4.7 out of 5 stars   
18       Apple iPhone 12 With FaceTime (128GB) - Blue  4.4 out of 5 stars   
19  Apple iPhone 12 Pro Max With FaceTime (128GB) ...  4.4 out of 5 stars   
20  SoundPEATS Air3 Wireless Earbuds Mini Bluetoot...  4.0 out of 5 stars   
21                 JBL In-Ear Headphones, Black, T110  4.2 out of 5 stars   
22  Sony WI-C200 Wireless In-ear Bluetooth Headpho...  3.7 out of 5 stars   
23  Xiaomi Redmi 9A Dual SIM, 32GB, 2GB RAM, 4G LT...  4.0 out of 5 stars   
24  Wireless Earbuds SoundPEATS TrueAir2 Bluetooth...  3.8 out of 5 stars   
25   New Apple iPhone 13 with FaceTime (256GB) - Blue  4.3 out of 5 stars   
26  Anker Soundcore Life Q30 Bluetooth Headphones,...  4.6 out of 5 stars   
27  Xiaomi Mi Box S - 4K Ultra HDR Android TV Stre...  4.2 out of 5 stars   
28  Apple Watch Series 6 (GPS, 44mm) - Blue Alumin...  4.6 out of 5 stars   
29  All-new Kindle Paperwhite (8GB) - Now with a 6...  4.4 out of 5 stars   
30  Kingston A400 SATA SSD Solid State Drive 2.5 I...  4.5 out of 5 stars   
31  Samsung Galaxy S21 5G | Pro Grade Triple Camer...  3.6 out of 5 stars   
32      Apple iPhone 12 With FaceTime (128GB) - White  4.4 out of 5 stars   
33  Apple Watch Series 6 (GPS, 40mm) - Gold Alumin...  4.6 out of 5 stars   
34                         ستيك مي للتلفزيون من شاومي  4.0 out of 5 stars   
35                 New Apple AirPods (3rd generation)  4.3 out of 5 stars   
36     Apple iPhone 12 With FaceTime (256GB) - Purple  4.4 out of 5 stars   
37  Anker PowerLine III USB-C to USB-C Cable USB-C...  5.0 out of 5 stars   
38  Xiaomi Redmi Note 10S, Dual SIM, 128GB, 6GB RA...  3.8 out of 5 stars   
39  EZVIZ C6N FHD Indoor Security Camera WiFi Smar...  4.3 out of 5 stars   
40  Anker Nano iPhone Charger, 20W PIQ 3.0 Durable...  4.2 out of 5 stars   
41  Anker USB C to Lightning Cable (6 ft), Powerli...  4.0 out of 5 stars   
42  SAMSUNG 980 PRO 500GB PCIe NVMe Gen4 Internal ...  4.8 out of 5 stars   
43  Bluetooth Wireless Headphones 40 Hours Playtim...  4.2 out of 5 stars   
44  Samsung Galaxy S21 Ultra 5G Android Smartphone...  3.8 out of 5 stars   
45  Samsung Galaxy S20 FE Dual SIM - 128GB, 8GB RA...  4.1 out of 5 stars   
46  Apple iPhone 12 Pro Max With FaceTime (256GB) ...  4.4 out of 5 stars   
47  Extension Cord with 3 Power Socket and 3 USB S...  3.9 out of 5 stars   
48  Samsung Galaxy S20 FE 4G Android Smartphone, 1...                 NaN   
49  SanDisk Ultra Micro SD Card Android - Class 10...  4.4 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             3.0          2           

# Best Sellers in   Electronics (Page 2)

In [16]:
url = 'https://www.amazon.sa/-/en/gp/bestsellers/electronics/ref=zg_bs_pg_2?ie=UTF8&pg=2'

In [17]:
response = requests.get(url)
response.status_code

200

In [18]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [19]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [20]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [21]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.4 out of 5 stars\n'

In [22]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [23]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

UGREEN USB C Cable 2M, Braided 100W Power Delivery PD Fast charge Cable 20V 5A USB C to USB C 2.0 Cable Compatible for iPad mini 6, MacBook Pro 2021, iPad Pro 12.9", Samsung S21, Huawei P40, etc
4.2 out of 5 stars
4.2
3,503
3503
SAR 40.80
40.80


In [24]:
soup.find_all("li", class_ = "zg-item-immersion")[1] 

<li class="zg-item-immersion" role="gridcell"><span class="a-list-item"><div class="a-section a-spacing-none aok-relative"><div class="a-row a-spacing-none aok-inline-block"><span class="a-size-small aok-float-left zg-badge-body zg-badge-color"><span class="zg-badge-text">#52</span></span><span class="aok-float-left zg-badge-triangle zg-badge-color"></span></div><span class="aok-inline-block zg-item"><a class="a-link-normal" href="/-/en/Apple-iPhone-Pro-FaceTime-128GB/dp/B08L5R1CCC?_encoding=UTF8&amp;psc=1"><span class="zg-text-center-align"><div class="a-section a-spacing-small"><img alt="Apple iPhone 12 Pro Max With FaceTime (128GB) - Graphite" height="200" src="https://images-na.ssl-images-amazon.com/images/I/71XXJC7V8tL._AC_UL200_SR200,200_.jpg" width="200"/></div></span>
<div aria-hidden="true" class="p13n-sc-truncate p13n-sc-line-clamp-2" data-rows="2">
            Apple iPhone 12 Pro Max With FaceTime (128GB) - Graphite
        </div>
</a>
<div class="a-icon-row a-spacing-none">

In [25]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [26]:
products_df2 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df2

pro_name            pro_rate  \
0   UGREEN USB C Cable 2M, Braided 100W Power Deli...  4.2 out of 5 stars   
1   Apple iPhone 12 Pro Max With FaceTime (128GB) ...  4.4 out of 5 stars   
2   Sony MDR-ZX110AP Extra Bass Smartphone Headset...  4.1 out of 5 stars   
3   MSI MPG Z490 Gaming Plus Gaming Motherboard (A...  4.6 out of 5 stars   
4   Anker PowerCore III 10K, Wireless Portable Cha...  4.7 out of 5 stars   
5   Glorious Large Gaming Mouse Pad 11''x13'' - Black  4.7 out of 5 stars   
6   UGREEN 2 Pack Screen Protector for iPhone 13/1...  4.4 out of 5 stars   
7                                   Apple AirPods Pro  4.3 out of 5 stars   
8   Stylus Pen for iPad with Palm Rejection，Active...  2.7 out of 5 stars   
9   Compatible with Apple Watch Case Series 4 Seri...  3.9 out of 5 stars   
10  TP-Link AC1750 Wi-Fi Range Extender - RE450, W...  4.0 out of 5 stars   
11  All-New Kindle Oasis (10th gen) - 7 Inch High-...  4.1 out of 5 stars   
12  Samsung Galaxy Note20 5G, Pro Grade Triple Cam...  4.1 out of 5 stars   
13  2021 Apple iPad Pro (11-inch, Wi-Fi, 128GB) - ...  4.6 out of 5 stars   
14        Apple iPhone 12 With FaceTime (64GB) - Blue  4.4 out of 5 stars   
15  Anker 30W PIQ 3.0 USB-C Fast Charger Adapter, ...  4.5 out of 5 stars   
16  SAMSUNG 870 QVO SATA III 2.5" SSD 1TB (MZ-77Q1...  4.8 out of 5 stars   
17  UGREEN Fast Car Charger Adapter 42.5W Dual USB...  4.3 out of 5 stars   
18  6 PCS Camera Cover,Sliding Webcam Cover,Ultra ...  4.4 out of 5 stars   
19  SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
20  ELON Fast Charging Cable for iPhone USB to Lig...  4.3 out of 5 stars   
21  UGREEN PD 20W Car Charger Fast Charging for iP...  4.3 out of 5 stars   
22  HP 652 Ink Advantage Cartridge, Tri-color - F6...  4.4 out of 5 stars   
23  Samsung Galaxy M11 Dual SIM - 32GB, 3GB RAM, 4...  4.0 out of 5 stars   
24  Xiaomi POCO X3 Pro, Dual SIM, 256GB, 8GB RAM, ...  4.2 out of 5 stars   
25  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
26  Anker 30W PIQ 3.0 USB-C Fast Charger Adapter, ...  4.5 out of 5 stars   
27  SanDisk Ultra Dual Drive USB Type-C Flash Driv...  4.4 out of 5 stars   
28  SoundPEATS Smart Watch New Upgraded 13 Sports ...  4.1 out of 5 stars   
29  HUAWEI FreeBuds 4i Wireless In-Ear Bluetooth E...  4.1 out of 5 stars   
30  UGREEN iPhone Charger PD20W USB C iPhone 13 Fa...  4.2 out of 5 stars   
31     Apple iPhone 12 With FaceTime (128GB) - Purple  4.4 out of 5 stars   
32  SAMSUNG 970 EVO Plus SSD 2TB - M.2 NVMe Interf...  4.9 out of 5 stars   
33  JBL CLIP4 WIRELESS PORTABLE SPEAKER - Blue/Pin...  4.7 out of 5 stars   
34    HP 652 Ink Advantage Cartridge, Black - F6V25AE  4.4 out of 5 stars   
35  ZORD PHANTOM-1 GAMING PC, RYZEN 3 3200G, 16GB ...  3.3 out of 5 stars   
36  Samsung Galaxy A72 | Ultra High-Res Quad Camer...  4.2 out of 5 stars   
37  Seagate BarraCuda 4TB Internal Hard Drive HDD ...  4.7 out of 5 stars   
38  Wireless Earbuds, SOUNDPEATS S5 Over-Ear Hooks...  4.4 out of 5 stars   
39   New Apple iPhone 13 with FaceTime (128GB) - Blue  4.3 out of 5 stars   
40  AMD Ryzen 9 5900X 12-core, 24-Thread Unlocked ...  4.8 out of 5 stars   
41  Anker Alkaline AAA Batteries (4-Pack), Long-La...  4.5 out of 5 stars   
42  Razer Seiren Mini - USB Condenser Microphone f...  4.6 out of 5 stars   
43  Apple iPhone 12 Pro With FaceTime (256GB) - Si...  4.2 out of 5 stars   
44  UGREEN Car Phone Mount Dashboard Car Holder Wi...  4.4 out of 5 stars   
45  UGREEN Magnetic Car Phone Holder Air Vent Moun...  4.0 out of 5 stars   
46  Thermal Grizzly Kryonaut 12.5 W / m · K 1 g th...  4.7 out of 5 stars   
47  UGREEN iPhone Protective Case Compatible for i...  4.5 out of 5 stars   
48  Samsung Galaxy S21 Dual SIM - 128GB, 8GB RAM, ...  3.6 out of 5 stars   
49  UGREEN USB C Cable 3A Fast Charging Cable Nylo...  4.3 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.2      3,503           

# Best Sellers in Camera & Photo Products (Page 1)

In [27]:
url = 'https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966385031/ref=zg_bs_nav_1_electronics'

In [28]:
response = requests.get(url)
response.status_code

200

In [29]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [30]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [31]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [32]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.3 out of 5 stars\n'

In [33]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [34]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

EZVIZ C6N Pan/Tilt Camera FHD Indoor,1080p WiFi Smart Home Security Camera IR Night Vision Motion Detection Auto Tracking Baby/Elder/Pet Cloud Storage/SD Slot 2-Way Audio Wi-Fi 2.4G iOS Android App
4.2 out of 5 stars
4.2
1,409
1409
SAR 98.00
98.00


In [35]:
soup.find_all("li", class_ = "zg-item-immersion")[1] 

<li class="zg-item-immersion" role="gridcell"><span class="a-list-item"><div class="a-section a-spacing-none aok-relative"><div class="a-row a-spacing-none aok-inline-block"><span class="a-size-small aok-float-left zg-badge-body zg-badge-color"><span class="zg-badge-text">#2</span></span><span class="aok-float-left zg-badge-triangle zg-badge-color"></span></div><span class="aok-inline-block zg-item"><a class="a-link-normal" href="/-/en/EZVIZ-Indoor-Security-Camera-Android/dp/B07ZC1Q6W6?_encoding=UTF8&amp;psc=1"><span class="zg-text-center-align"><div class="a-section a-spacing-small"><img alt="EZVIZ C6N FHD Indoor Security Camera WiFi Smart 2.4G with iOS and Android App" height="200" src="https://images-na.ssl-images-amazon.com/images/I/51bA8A2cU9L._AC_UL200_SR200,200_.jpg" width="200"/></div></span>
<div aria-hidden="true" class="p13n-sc-truncate p13n-sc-line-clamp-2" data-rows="2">
            EZVIZ C6N FHD Indoor Security Camera WiFi Smart 2.4G with iOS and Android App
        </div

In [36]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [37]:
products_df3 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df3

pro_name            pro_rate  \
0   EZVIZ C6N Pan/Tilt Camera FHD Indoor,1080p WiF...  4.2 out of 5 stars   
1   EZVIZ C6N FHD Indoor Security Camera WiFi Smar...  4.3 out of 5 stars   
2   SanDisk Ultra Micro SD Card Android - Class 10...  4.4 out of 5 stars   
3   6 PCS Camera Cover,Sliding Webcam Cover,Ultra ...  4.4 out of 5 stars   
4   eufy Security, eufyCam 2 Pro Wireless Home Sec...  4.5 out of 5 stars   
5   SanDisk Ultra microSDXC 128GB 100MB/s Class 10...  4.4 out of 5 stars   
6   Eufy Indoor Cam 2K Pan & Tilt Home Security Ca...  4.5 out of 5 stars   
7         SanDisk Extreme microSDXC UHS-I Card- 128GB  4.4 out of 5 stars   
8         Xiaomi Mi Home Security Camera 360° - White  4.0 out of 5 stars   
9   AmazonBasics Braided 4K HDMI to HDMI Cable - 3...  4.7 out of 5 stars   
10    Kioxia Exceria 64GB MicroSD Card - LMEX1L064GG2  4.6 out of 5 stars   
11  DJI Osmo Mobile 3 Combo - 3-Axis Gimbal Stabil...  4.6 out of 5 stars   
12   KIOXIA Exceria 32GB Micro SD Card - LMEX1L032GG2  4.6 out of 5 stars   
13       Canon EOS Digital Camera, Black - 250D 18-55  4.5 out of 5 stars   
14  Imou 360 Degree Security Camera,Up to 256GB SD...  4.3 out of 5 stars   
15  Neewer 50-In-1 Action Camera Accessory Kit, Co...  4.4 out of 5 stars   
16  UGREEN 8K HDMI 2.1 Cable Ultra High-Speed 48Gb...  4.6 out of 5 stars   
17                 Rode Dynamic Podcasting Microphone  4.8 out of 5 stars   
18  SanDisk 128GB Ultra® microSDXC 120MB/s A1 Clas...  4.4 out of 5 stars   
19        SanDisk Extreme microSDXC UHS-I Card- 512GB  4.4 out of 5 stars   
20  Selfie Stick Tripod,Eocean 40 inch Extendable ...  4.0 out of 5 stars   
21  YG-300 LCD Mini Portable Projector with USB/SD...  2.6 out of 5 stars   
22  UGREEN 8K DisplayPort Cable Ultra HD DisplayPo...  4.6 out of 5 stars   
23     Fujifilm Instax Mini, 10 sheet x 2 pack, White  4.6 out of 5 stars   
24  EZVIZ Wifi Smart Security Camera 360 Degree, D...  4.2 out of 5 stars   
25  Professional Camera Tripod Mount Stand Holder ...  2.1 out of 5 stars   
26  AmazonBasics High-Speed 4K HDMI Cable, 3 Feet,...  4.6 out of 5 stars   
27     Sony Cyber-Shot DSC-W800-20.1 MegaPixel, Black  4.0 out of 5 stars   
28        Canon EF 50mm f/1.8 STM Standard Lens,Black  4.8 out of 5 stars   
29  Imou 360 Degree WiFi Security Camera, Up to 25...  3.1 out of 5 stars   
30  UGREEN 8K HDMI Cable Ultra HD High Speed 48Gbp...  4.6 out of 5 stars   
31  eufy Security, eufyCam 2 Pro Wireless Home Sec...  4.5 out of 5 stars   
32  2 Meters LED Strip Light, TV Bias Backlighting...  3.3 out of 5 stars   
33  Panasonic Eneloop Pro Individual Cell Battery ...  4.0 out of 5 stars   
34  eufy Security 2K Indoor Cam Pan & Tilt, Home S...  4.6 out of 5 stars   
35  UGREEN 4K UHD DP to HDMI Cable Male to Male Di...  4.5 out of 5 stars   
36                              eufyCam 2C pro Add on                 NaN   
37  SanDisk 512GB Ultra MicroSDXC UHS-I Memory Car...  4.8 out of 5 stars   
38  SanDisk Ultra microSDXC 64GB 100MB/s Class 10 ...  4.4 out of 5 stars   
39                         Apple Pencil Tips - 4 pack  4.8 out of 5 stars   
40  EZVIZ C6TC, 1080p WiFi Smart Home Security Cam...  4.4 out of 5 stars   
41  opula Screen Cleaning Kit, Spray, Small Towel ...  4.7 out of 5 stars   
42  SanDisk Extreme PRO 256GB SDXC Memory Card up ...  4.8 out of 5 stars   
43       SanDisk Ultra 128GB SDXC Memory Card 120MB/s  4.7 out of 5 stars   
44  Imou 4MP Full HD, IP 67 Outdoor Bullet Securit...  3.0 out of 5 stars   
45  NATNO 3-in-1 USB Battery Charger Replacement f...                 NaN   
46  Fujifilm Instax Mini Film For Instax Mini 7 / ...  4.4 out of 5 stars   
47  eufy Security eufyCam 2 Wireless Home Security...  4.5 out of 5 stars   
48  BOYA BY M1 Lavalier Microphone for Smartphones...  3.9 out of 5 stars   
49  SanDisk 32GB Ultra® microSDHC 120MB/s A1 Class...  4.4 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.2      1,409           

# Best Sellers in Camera & Photo Products (Page 2)

In [38]:
url ='https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966385031/ref=zg_bs_pg_2?ie=UTF8&pg=2'

In [39]:
response = requests.get(url)
response.status_code

200

In [40]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [41]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [42]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [43]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.3 out of 5 stars\n'

In [44]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [45]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

AccLoo Mini WiFi Camera, HD 1080P Wireless Portable Small Camera with Motion Detection and Night Version Home Security Cameras Nanny Cam Video Recorder for Room, Office
3.4 out of 5 stars
3.4
19
19
SAR 128.47
128.47


In [46]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [47]:
products_df4 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df4

pro_name            pro_rate  \
0   AccLoo Mini WiFi Camera, HD 1080P Wireless Por...  3.4 out of 5 stars   
1        Celestron Portable Telescope Travel Scope 70  4.3 out of 5 stars   
2   150 inch Projector Screen for Movies, 16:9 HD ...  3.8 out of 5 stars   
3   Fujifilm Instax Mini Instant Film - 60 Sheets ...  4.6 out of 5 stars   
4   2 * 2m/6.6 * 6.6ft Studio Backdrop Stand Brack...  3.3 out of 5 stars   
5   Microphone Stand Set Heavy Duty Mic Suspension...  3.5 out of 5 stars   
6   UGREEN Micro HDMI to HDMI Adapter Cable Male t...  4.6 out of 5 stars   
7   UGREEN 8K DisplayPort Cable Ultra HD DisplayPo...  4.6 out of 5 stars   
8   SanDisk 256GB microSDXC Card, Licensed for Nin...  4.9 out of 5 stars   
9         SanDisk Extreme microSDXC UHS-I Card- 256GB  4.4 out of 5 stars   
10  SanDisk 256GB Ultra® microSDXC 120MB/s A1 Clas...  4.4 out of 5 stars   
11  EZVIZ C2C 1080P Smart Home Security Wifi Camer...                 NaN   
12  UGREEN 8K DisplayPort Cable Ultra HD DisplayPo...  4.6 out of 5 stars   
13  AccLoo Kids Camera 1080P HD Digital Video Toy ...  3.8 out of 5 stars   
14  FiTSTILL Waterproof Protective Underwater 60M ...  4.6 out of 5 stars   
15  SanDisk 400GB Ultra® microSDXC 120MB/s A1 Clas...  4.4 out of 5 stars   
16  UGREEN 8K HDMI Cable Ultra HD High Speed 48Gbp...  4.6 out of 5 stars   
17  Sandisk Extreme microSDXC 128GB Plus SD Adapte...  4.8 out of 5 stars   
18  eufy Security 2K Indoor Cam, Home Security Ind...  4.5 out of 5 stars   
19  FunLites Upgraded Full HD Projector, Native 10...  4.1 out of 5 stars   
20  Selfie Stick Tripod, Eocean 54 inch Extendable...  4.3 out of 5 stars   
21  Ametoys 16:9 Projector Screen Stable Base Pipe...                 NaN   
22  Imou 4MP FHD 360 Degree Security Camera (White...  3.0 out of 5 stars   
23  Fujifilm Instax mini 9 Instant Film Camera, Ic...  3.2 out of 5 stars   
24  Luckydoor M500 Android 6.0 Handheld Wireless P...                 NaN   
25  Xiaomi Mi Home Security Camera 360 Degrees 2K ...  4.2 out of 5 stars   
26  Fujifilm Instax Wide Film Twin Pack (White) (N...  4.8 out of 5 stars   
27          SanDisk Extreme microSDXC UHS-I Card- 1TB  4.4 out of 5 stars   
28  FitStill 3 Way Tripod for GoPro Hero 10/9/8/7/...  4.3 out of 5 stars   
29  Andoer Photography Studio Cube Umbrella Softbo...  4.0 out of 5 stars   
30  Waterproof Anti-Shock DSLR Camera Bag for Cano...  4.3 out of 5 stars   
31  YSK-Replacement Remote control for Class pro s...  5.0 out of 5 stars   
32  Portable Universal Tripod Stand Adjustable For...  2.3 out of 5 stars   
33  Podcast Equipment Bundle, Condenser Microphone...  2.7 out of 5 stars   
34  100 inch Projector Screen with Stand, 16:9 HD ...  4.6 out of 5 stars   
35  UGREEN 8K HDMI 2.1 Cable Ultra High-Speed 48Gb...  4.6 out of 5 stars   
36  6pcs Computer Keyboard Cleaning Brush Kit Nylo...  3.2 out of 5 stars   
37  JF-3110 35-102cm Aluminum Alloy Tripod Portabl...  2.4 out of 5 stars   
38  GoPro Rechargeable Battery for HERO9 Black, AD...  4.7 out of 5 stars   
39  EZVIZ C1C-B WiFi Security Camera, 12 Meters Ni...  4.1 out of 5 stars   
40  Pepisky USB LED Video Light Kit,Photography Li...                 NaN   
41  Sandisk 128 GB Memory Card For Multi - Micro S...  4.2 out of 5 stars   
42  SanDisk 32GB Ultra microSDHC UHS-I Memory Card...  4.7 out of 5 stars   
43  AccLoo WiFi Camera, HD 1080P Wireless Camera w...  3.9 out of 5 stars   
44  Canon EOS 2000D 18-55 IS, 24.1 MP, DSLR Camera...  4.7 out of 5 stars   
45  Professional Lavalier Microphone,AGPTEK Clip-o...  3.9 out of 5 stars   
46  SKYRC iMAX B6 V2 Balance Charger 60W 6A DC/DC ...  5.0 out of 5 stars   
47  Mini Camera,Phomnd Mini Camera Cordless WiFi R...  5.0 out of 5 stars   
48  Star Projector, AMINAC LED Galaxy Light Projec...  5.0 out of 5 stars   
49  GoPro HERO9 Action Camera Black, Waterproof wi...  4.4 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             3.4         19           

# Best Sellers in Binoculars, Telescopes & Optics (Page 1) 

In [48]:
url ="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966400031/ref=zg_bs_nav_2_16966385031"


In [49]:
response = requests.get(url)
response.status_code

200

In [50]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [51]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [52]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [53]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.3 out of 5 stars\n'

In [54]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [55]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Apple Pencil Tips - 4 pack
4.8 out of 5 stars
4.8
8
8
SAR 98.00
98.00


In [56]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [57]:
products_df5 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df5

pro_name            pro_rate  \
0                          Apple Pencil Tips - 4 pack  4.8 out of 5 stars   
1        Celestron Portable Telescope Travel Scope 70  4.3 out of 5 stars   
2   (Single Pack) - Carson MicroBrite Plus 60 -120...  4.2 out of 5 stars   
3   Celestron UpClose G2 10x25 Monocular, Black (7...  4.0 out of 5 stars   
4   Celestron - 50mm Travel Scope - Portable Refra...  3.8 out of 5 stars   
5         Steiner 5845 7X50 Sagor II Binocular, Green  5.0 out of 5 stars   
6   National Geographic 50Mm Telescope For Kids by...  3.7 out of 5 stars   
7   Telescope Phone Mount, Universal Smart Phone A...  3.5 out of 5 stars   
8                    Bushnell Trophy Xtreme Binocular  4.6 out of 5 stars   
9                         PROFESSIONAL COOLING SYSTEM  5.0 out of 5 stars   
10              Bushnell 10x42 Binocular منظار بوشنيل  3.4 out of 5 stars   
11  Bushnell Falcon 10x50 Wide Angle Binoculars - ...  4.5 out of 5 stars   
12  Docooler Lens Telescope 16x52 Telescope Monocu...                 NaN   
13  10X25 Small Compact Lightweight Binoculars for...  3.3 out of 5 stars   
14  40X60 HD Mini Day and Night Vision Monocular T...  3.1 out of 5 stars   
15  Celestron - 70mm Travel Scope DX - Portable Re...  4.2 out of 5 stars   
16  ComCreate 8X Folding High Powered Binoculars W...  1.0 out of 5 stars   
17  Steiner Peregrine Binoculars, Perfect for Wild...  4.2 out of 5 stars   
18           Celestron 21039 PowerSeeker 50 Telescope  4.1 out of 5 stars   
19       Celestron 93230 8 to 24mm 1.25 Zoom Eyepiece  4.7 out of 5 stars   
20  Celestron 93529 X-Cel LX 1.25-Inch 2x Barlow L...  4.7 out of 5 stars   
21  Garberiel Monocular Telescope 12X50 High Power...  1.7 out of 5 stars   
22  Jiusion 40 to 1000x Magnification Endoscope, 2...  4.2 out of 5 stars   
23  Telescope, 70mm Aperture 400mm AZ Mount Astron...                 NaN   
24  Nikon BAA807SB Fernglas Aculon A30 8x25 Binocu...  4.5 out of 5 stars   
25  Celestron - PowerSeeker 127EQ Telescope - Manu...  4.2 out of 5 stars   
26  Nikon 7246 Action 12x50 EX Extreme All-Terrain...  4.6 out of 5 stars   
27  Celestron 21045 PowerSeeker 114EQ Telescope - ...  4.1 out of 5 stars   
28             Steiner 8X30 Sagor II Binocular, Green  5.0 out of 5 stars   
29  Celestron 93428 X-Cel LX 1.25-Inch 3x Barlow L...  4.6 out of 5 stars   
30  Baigaish Binocular 20x50 HD Professional/Water...                 NaN   
31  8x21 Kids Binoculars Set - High Resolution Rea...  4.0 out of 5 stars   
32    Celestron StarSense Explorer DX 130AZ Telescope  4.3 out of 5 stars   
33  NATIONAL GEOGRAPHIC Junior Metal Detector –Adj...  4.2 out of 5 stars   
34      Sunagor Mega Zoom Binoculars 30-160x70 ,Black  3.7 out of 5 stars   
35  Sunagor Compact Zoom Binoculars 25-110x30,Silv...  3.7 out of 5 stars   
36                        Celestron 1.25" Moon Filter  4.1 out of 5 stars   
37      Bushnell Legend Ultra HD Roof Prism Binocular  4.6 out of 5 stars   
38  Celestron – Outland X 8x42 Binoculars – Waterp...  4.5 out of 5 stars   
39  Built in Motion Plus Remote and Nunchuck Contr...                 NaN   
40  Panasonic P-6JRC Replacement Water Filter Cart...  4.6 out of 5 stars   
41  Celestron - SkyMaster 25x70 Binocular - Large ...  4.4 out of 5 stars   
42  HEXEUM Night Vision Goggles Night Vision Binoc...  4.6 out of 5 stars   
43  Telescope Star Finder with Tripod F36050 HD Zo...  3.3 out of 5 stars   
44  SCOKC Binoculars 20x50 High Power, Compact HD ...  4.7 out of 5 stars   
45  HUTACT 10x42 Binoculars for Adults, with Stora...  4.4 out of 5 stars   
46  10X22 Binocular Telescope Night Version Foldab...  2.7 out of 5 stars   
47  ARCTIC P12 PWM (Black/Black) - Pressure-optimi...  4.6 out of 5 stars   
48  Gskyer Telescope, 70mm Aperture 400mm AZ Mount...  4.4 out of 5 stars   
49  DMG-Digital Microscope 50x To 1000x Magnificat...  3.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.8          8           

# Best Sellers in Binoculars, Telescopes & Optics (Page 2)

In [58]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966400031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [59]:
response = requests.get(url)
response.status_code

200

In [60]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [61]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [62]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [63]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'SAR 149.99'

In [64]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [65]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Camera Diaphragm, Compact Iris Aperture Adjustable for Industry for Home for Optical Instruments for Laboratory for Workshop




SAR 195.89
195.89


In [66]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [67]:
products_df6 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df6

pro_name            pro_rate  \
0   Camera Diaphragm, Compact Iris Aperture Adjust...                 NaN   
1   12X50 HD Monocular Telescope with Quick Smartp...                 NaN   
2   Bysameyee USB Digital Microscope 40X to 1000X,...  3.0 out of 5 stars   
3   Mega Sports 10X25 Compact Binocular for Bird W...                 NaN   
4   12x42 Binoculars for Adults with New Smartphon...  4.8 out of 5 stars   
5   Newdoar 25x30 Zoomable Monocular Vintage Pirat...  4.2 out of 5 stars   
6            Nikon Aculon A211 7x50 Binoculars, Black  4.6 out of 5 stars   
7   2021 Newest Telescope, 60mm Aperture 500mm AZ ...                 NaN   
8                  Vortex Optics Solo Monocular 10x25  4.4 out of 5 stars   
9   SCOKC 10x-20x Zoom Binoculars Monocular HD Pow...  4.3 out of 5 stars   
10  Carson MicroFlip 100x-250x LED Lighted Pocket ...  4.1 out of 5 stars   
11  Celestron - NexStar 127SLT Computerized Telesc...  4.3 out of 5 stars   
12             10X42 Darbel Bushnell Sport Roof Prism  3.6 out of 5 stars   
13  Celestron Upclose 20x50 Binoculars Porro Prism...  4.0 out of 5 stars   
14  Celestron – Outland X 10x50 Binoculars – Water...  4.5 out of 5 stars   
15                Opticron BGA 10x42 Monocular, black  4.7 out of 5 stars   
16  10x34 glasses type low light night vision tele...  2.4 out of 5 stars   
17  NIKULA metal High powered telescope zoom porta...  1.6 out of 5 stars   
18  SOOBA Astronomical Telescope Compact Portable ...                 NaN   
19  Steiner Marine Binoculars for Adults and Kids,...  4.8 out of 5 stars   
20  Celestron - PowerSeeker 70AZ Telescope - Manua...  4.2 out of 5 stars   
21  8"x8" Solar Filter Sheet for Telescopes, Binoc...                 NaN   
22  Celestron 93524 Roof and Porro Binocular Tripo...  4.3 out of 5 stars   
23   Bushnell Monoculars Telescope 16x52 Lens - Black  3.1 out of 5 stars   
24  Steiner 4477 10X26 Safari Ultrasharp Binocular...  4.5 out of 5 stars   
25             قاعدة تصوير دربيل او ناظور صيد احترافي                 NaN   
26  Balacoo Monocular Telescope 40x60 High Definit...                 NaN   
27  Phone JJone APL-JS60XJJ09 Metal 60X HD Phone T...                 NaN   
28  Bushnell Equinox Z Night Vision 6X50 EQUINOX Z...  4.0 out of 5 stars   
29  ARCTIC ACFAN00135A P12 Value Pack - Pressure-O...  4.6 out of 5 stars   
30  KA Monocular Telescope fo Phone, 40X60 HD Mono...                 NaN   
31  Celestron - PowerSeeker Telescope Accessory Ki...  4.6 out of 5 stars   
32   Celestron 93317 Omni Series 1.25" (6mm) Eyepiece  4.6 out of 5 stars   
33  12X50 Powerful Binoculars, High Power HD Binoc...  4.3 out of 5 stars   
34  10x22 Binoculars Professional Telescope Zoom V...                 NaN   
35  Celestron - Cometron 7x50 Bincoulars - Beginne...  4.6 out of 5 stars   
36                 Steiner Military-Marine Binoculars  4.6 out of 5 stars   
37         Panda 35x50 Adjustable Monocular Telescope  2.9 out of 5 stars   
38  Binoculars for Kids - HIGH Resolution, Shockpr...  4.5 out of 5 stars   
39  Astronomy Refractor Telescope, High Definition...                 NaN   
40  National Geographic 90-01001 50/600 Refractor ...  3.8 out of 5 stars   
41  Joshjt Telescope 70mm Aperture 400mm AZ Mount,...                 NaN   
42  Bushnell Powerview Compact Folding Roof Prism ...  4.3 out of 5 stars   
43  60X60 Binoculars Telescope, Night Vision 10000...                 NaN   
44  DECUHTE Portable Mini Monocular Telescope with...                 NaN   
45  Vortex Optics Crossfire HD 10x50 Binoculars, B...  4.8 out of 5 stars   
46  Scienish Telescope Travel Scope 90 X Refractor...  5.0 out of 5 stars   
47              Panda 35X50 Zoom Monoculars Telescope  2.1 out of 5 stars   
48  60x60 binocular with coordinates night vision ...                 NaN   
49  Portable monocular, 40X60 HD Low-Light Night V...  1.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             NaN        NaN           

# Best Sellers in Computers, Components & Accessories (Page 1)

In [68]:
url= " https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966388031/ref=zg_bs_nav_1_electronics"

In [69]:
response = requests.get(url)
response.status_code

200

In [70]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [71]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [72]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [73]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.1 out of 5 stars\n'

In [74]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [75]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Stylus Pen for iPad with Palm Rejection, Active Pencil Compatible with (2018-2021) iPad Pro 11 & 12.9 inch, iPad 9th/8th/7th/6th Gen, iPad Air 4th/3rd Gen,iPad Mini 6th/5th Gen
3.4 out of 5 stars
3.4
5,548
5548
SAR 58.77
58.77


In [76]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [77]:
products_df7 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df7

pro_name            pro_rate  \
0   Stylus Pen for iPad with Palm Rejection, Activ...  3.4 out of 5 stars   
1   530pcs/set Heat Shrink Tubing Insulation Shrin...  4.1 out of 5 stars   
2   Kingston A400 SATA SSD Solid State Drive 2.5 I...  4.5 out of 5 stars   
3   Anker PowerLine III USB-C to USB-C Cable USB-C...  5.0 out of 5 stars   
4   Anker USB C to Lightning Cable (6 ft), Powerli...  4.0 out of 5 stars   
5   SAMSUNG 980 PRO 500GB PCIe NVMe Gen4 Internal ...  4.8 out of 5 stars   
6   SanDisk Ultra Micro SD Card Android - Class 10...  4.4 out of 5 stars   
7   UGREEN USB C Cable 2M, Braided 100W Power Deli...  4.2 out of 5 stars   
8   MSI MPG Z490 Gaming Plus Gaming Motherboard (A...  4.6 out of 5 stars   
9   Glorious Large Gaming Mouse Pad 11''x13'' - Black  4.7 out of 5 stars   
10  Stylus Pen for iPad with Palm Rejection，Active...  2.7 out of 5 stars   
11  TP-Link AC1750 Wi-Fi Range Extender - RE450, W...  4.0 out of 5 stars   
12  2021 Apple iPad Pro (11-inch, Wi-Fi, 128GB) - ...  4.6 out of 5 stars   
13  SAMSUNG 870 QVO SATA III 2.5" SSD 1TB (MZ-77Q1...  4.8 out of 5 stars   
14  SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
15  ELON Fast Charging Cable for iPhone USB to Lig...  4.3 out of 5 stars   
16  HP 652 Ink Advantage Cartridge, Tri-color - F6...  4.4 out of 5 stars   
17  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
18  SanDisk Ultra Dual Drive USB Type-C Flash Driv...  4.4 out of 5 stars   
19  SAMSUNG 970 EVO Plus SSD 2TB - M.2 NVMe Interf...  4.9 out of 5 stars   
20    HP 652 Ink Advantage Cartridge, Black - F6V25AE  4.4 out of 5 stars   
21  ZORD PHANTOM-1 GAMING PC, RYZEN 3 3200G, 16GB ...  3.3 out of 5 stars   
22  Seagate BarraCuda 4TB Internal Hard Drive HDD ...  4.7 out of 5 stars   
23  AMD Ryzen 9 5900X 12-core, 24-Thread Unlocked ...  4.8 out of 5 stars   
24  Razer Seiren Mini - USB Condenser Microphone f...  4.6 out of 5 stars   
25  Thermal Grizzly Kryonaut 12.5 W / m · K 1 g th...  4.7 out of 5 stars   
26  UGREEN USB C Cable 3A Fast Charging Cable Nylo...  4.3 out of 5 stars   
27  Samsung Electronics A7 Tablet 10.4 Wi-Fi 64GB ...  4.1 out of 5 stars   
28  UGREEN iPhone Lightning Cable 2M [MFi Certifie...  4.6 out of 5 stars   
29  UGREEN iPhone 13 Charger Cable [MFi Certified]...  4.1 out of 5 stars   
30  Corsair Vengeance LPX 16GB (2 X 8GB) DDR4 3600...  4.8 out of 5 stars   
31  HP 123 Black Original Ink Advantage Cartridge ...  4.1 out of 5 stars   
32  SanDisk Ultra Dual Drive Luxe USB Type-C 128GB...  4.4 out of 5 stars   
33  Logitech M171 Wireless Mouse, 2.4 GHz with USB...  4.4 out of 5 stars   
34  2Pack Apple Original Charger [Apple MFi Certif...  4.5 out of 5 stars   
35  UGREEN USB C Cable 3A Fast Charging Cable Nylo...  4.3 out of 5 stars   
36  iPhone Charger Lightning Cable 10ft - by TalkW...  4.1 out of 5 stars   
37  WD 5TB My Passport Portable External Hard Driv...  4.3 out of 5 stars   
38  5-Socket Extension Cord with Individual on/off...  4.2 out of 5 stars   
39  Large Gaming Mousepad World Map Game Mouse Pad...  4.3 out of 5 stars   
40  Desk, Laptop Desk Bed Foldable Lazy Small Tabl...  3.9 out of 5 stars   
41  UGREEN USB C Cable USB A to Type C Data Cable ...  4.4 out of 5 stars   
42  SAMSUNG 980 PRO 1TB PCIe NVMe Gen4 Internal Ga...  4.8 out of 5 stars   
43  Linksys WAP1200AC WiFi Access Point (AC1200 Si...  3.3 out of 5 stars   
44         Anker Powerline+ II 6 Foot Lightning Cable  4.1 out of 5 stars   
45  Precision Screwdriver Set,ShowTop 110 in 1 Mag...  3.8 out of 5 stars   
46  New Office 2021 Pro For Windows | Lifetime Act...  5.0 out of 5 stars   
47  Asus Gaming Monitor - 27inch, Full HD, 0.5ms, ...  4.6 out of 5 stars   
48  SanDisk Ultra microSDXC 128GB 100MB/s Class 10...  4.4 out of 5 stars   
49  Laptop Stand, BiuLing Adjustable Portable Lapt...  3.6 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             3.4      5,548           

 # Best Sellers in Computers, Components & Accessories (Page 2)

In [78]:
url ="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966388031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [79]:
response = requests.get(url)
response.status_code

200

In [80]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [81]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [82]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [83]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.5 out of 5 stars\n'

In [84]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [85]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

SanDisk SSD PLUS 240GB - 2.5” SATA SSD, up to 530MB/s Read and 440MB/s Write speeds
4.7 out of 5 stars
4.7
60,635
60635
SAR 119.00
119.00


In [86]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [87]:
products_df8 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df8

pro_name            pro_rate  \
0   SanDisk SSD PLUS 240GB - 2.5” SATA SSD, up to ...  4.7 out of 5 stars   
1   Stylus Pen for iPad with Palm Rejection, Activ...  4.5 out of 5 stars   
2   SteelSeries Arctis 7 - Lossless Wireless Gamin...  4.5 out of 5 stars   
3   SAMSUNG (MZ-V7S1T0B/AM) 970 EVO Plus SSD 1TB -...  4.9 out of 5 stars   
4   TP-Link AC1300 USB WiFi Adapter(Archer T3U)- 2...  4.5 out of 5 stars   
5   Kingston 240GB A400 Sata 3 2.5 inch Internal S...  4.5 out of 5 stars   
6                      ZORD M27 GAMING MONITOR 27INCH  3.8 out of 5 stars   
7   UGREEN USB 3.0 Hub 4 Port USB 3 Data Hub Porta...  4.5 out of 5 stars   
8   Toshiba 1TB Canvio Basics Portable USB3.0 Hard...  4.6 out of 5 stars   
9   90x40cm Old World Map mouse pad large pad to m...  4.3 out of 5 stars   
10  ProCase iPad Pro 11 Case 2021 2020 2018, Slim ...  4.3 out of 5 stars   
11        SanDisk Extreme microSDXC UHS-I Card- 128GB  4.4 out of 5 stars   
12  Acer KG241QS - 23.6" (Full HD)1920 x 1080 over...  4.4 out of 5 stars   
13  TKOOFN Large RGB Colorful LED Light Keyboard M...  3.8 out of 5 stars   
14  [2 Pack] ProCase Galaxy Tab S7 11 inch 2020 Sc...  4.3 out of 5 stars   
15  UGREEN iPhone Lightning Cable [MFi Certified] ...  4.1 out of 5 stars   
16  SanDisk Ultra Dual Drive USB Type-C Flash Driv...  4.4 out of 5 stars   
17  Stylus Pen for iPad with Palm Rejection, Activ...  4.6 out of 5 stars   
18  Anker Powerline Micro USB - Charging Cable, wi...  4.3 out of 5 stars   
19  Logitech MK235 Wireless Keyboard and Mouse Com...  3.8 out of 5 stars   
20  WD Blue SN550 500GB NVMe Internal SSD - Gen3 x...  4.6 out of 5 stars   
21  SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
22  ProCase iPad Air 4 Screen Protector 10.9 2020/...  4.6 out of 5 stars   
23  AmazonBasics Braided 4K HDMI to HDMI Cable - 3...  4.7 out of 5 stars   
24  HyperX QuadCast - USB Condenser Gaming Microph...  4.8 out of 5 stars   
25  YEFOOT iPhone Charger [MFi Certified] 6Pack[3/...  4.4 out of 5 stars   
26  UGREEN USB C Cable 1M, Braided 100W Power Deli...  4.2 out of 5 stars   
27  AmazonBasics USB 2.0 A-Male to Micro B Charger...  4.5 out of 5 stars   
28  Western Digital WDS500G2B0A WD Blue 3D NAND In...  4.7 out of 5 stars   
29  USB C 9-in1 Hub with 4K HDMI Adapter 100W PD C...  4.4 out of 5 stars   
30  YISK Store Extended Large Gaming Mouse Pad XL ...  4.2 out of 5 stars   
31  Microsoft Wireless Mobile Mouse 1850, Black [U...  4.3 out of 5 stars   
32  Belkin USB-C to Lightning Cable (iPhone Fast C...  4.5 out of 5 stars   
33  Samsung Electronics (MZ-V8V1T0B/AM) 980 SSD 1T...  4.8 out of 5 stars   
34  Ajazz AK33 Blue Switch Backlight Mechaincal Ga...  3.9 out of 5 stars   
35    Kioxia Exceria 64GB MicroSD Card - LMEX1L064GG2  4.6 out of 5 stars   
36  Anti-Skid Mousepad Extended Super Large World ...  4.0 out of 5 stars   
37  2021 Apple 10.2-inch iPad (Wi-Fi, 64GB) - Spac...  4.2 out of 5 stars   
38  UGREEN Micro USB Cable Nylon Braided Fast Quic...  4.6 out of 5 stars   
39          TP-LINK AC1200 Wi-Fi Range Extender RE305  4.1 out of 5 stars   
40  UGREEN 7-in-1 USB C Hub 4K@60Hz Type C to HDMI...  4.2 out of 5 stars   
41  TP-Link AC1200 Whole-Home Mesh Wi-Fi System(DE...  4.2 out of 5 stars   
42  WD_BLACK 1TB SN750 SE NVMe Internal Gaming SSD...                 NaN   
43  محرك أقراص صلبة داخلي باراكودا من سيجيت سعة 2 ...  4.7 out of 5 stars   
44  UGREEN SD Card Reader USB 3.0/USB C OTG Dual S...  4.5 out of 5 stars   
45     Anker PowerLine Micro USB 3ft White Offline V3  4.1 out of 5 stars   
46  [2 Pack] ProCase Galaxy Tab A7 10.4 2020 Scree...  4.3 out of 5 stars   
47  UGREEN USB Bluetooth 4.0 Adapter USB Wireless ...  4.1 out of 5 stars   
48  UGREEN USB C Cable USB A to Type C Data Cable ...  4.4 out of 5 stars   
49  iPhone Fast Charger Cable, 【Apple MFi Certifie...  1.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             4.7     60,635            6

# Best Sellers in Headphones, Earbuds & Accessories (Page 1 )

In [88]:
url = "https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966390031/ref=zg_bs_pg_1?ie=UTF8&pg=1"

In [89]:
response = requests.get(url)
response.status_code

200

In [90]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [91]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [92]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [93]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.3 out of 5 stars\n'

In [94]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [95]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Apple AirPods with Charging Case
4.1 out of 5 stars
4.1
2,777
2777
SAR 475.00
475.00


In [96]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [97]:
products_df9 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df9

pro_name            pro_rate  \
0                    Apple AirPods with Charging Case  4.1 out of 5 stars   
1                               New Apple Airpods Pro  4.3 out of 5 stars   
2   Sony WH-1000XM4 Wireless Noise Cancelling Blue...  4.4 out of 5 stars   
3   SoundPEATS Air3 Wireless Earbuds Mini Bluetoot...  4.0 out of 5 stars   
4                  JBL In-Ear Headphones, Black, T110  4.2 out of 5 stars   
5   Sony WI-C200 Wireless In-ear Bluetooth Headpho...  3.7 out of 5 stars   
6   Wireless Earbuds SoundPEATS TrueAir2 Bluetooth...  3.8 out of 5 stars   
7   Anker Soundcore Life Q30 Bluetooth Headphones,...  4.6 out of 5 stars   
8                  New Apple AirPods (3rd generation)  4.3 out of 5 stars   
9   Bluetooth Wireless Headphones 40 Hours Playtim...  4.2 out of 5 stars   
10  Sony MDR-ZX110AP Extra Bass Smartphone Headset...  4.1 out of 5 stars   
11                                  Apple AirPods Pro  4.3 out of 5 stars   
12  HUAWEI FreeBuds 4i Wireless In-Ear Bluetooth E...  4.1 out of 5 stars   
13  Wireless Earbuds, SOUNDPEATS S5 Over-Ear Hooks...  4.4 out of 5 stars   
14  JBL T110 Wired Universal In-Ear Headphone with...  4.2 out of 5 stars   
15  Wireless Earbuds True Wireless Bluetooth Earph...  4.0 out of 5 stars   
16  Bose Noise Cancelling Wireless Bluetooth Headp...  4.5 out of 5 stars   
17  Bose QuietComfort Earbuds - True Wireless Nois...  4.4 out of 5 stars   
18  Hybrid Active Noise Cancelling Headphones with...  4.8 out of 5 stars   
19  Bose Noise Cancelling Wireless Bluetooth Headp...  4.5 out of 5 stars   
20    Apple Lightning to 3.5mm Headphone Jack Adapter  4.2 out of 5 stars   
21  Wireless Earbuds SoundPEATS TrueAir2 Bluetooth...  3.8 out of 5 stars   
22  Anker Soundcore Life P2 Wireless Earbuds with ...  4.2 out of 5 stars   
23  Sony WF-1000XM4 Industry Leading Noise Cancell...  3.9 out of 5 stars   
24    Huawei Sport lite Bluetooth Headset AM61, Black  4.0 out of 5 stars   
25  SoundPEATS Wireless Earbuds Bluetooth 5.0 Head...  3.9 out of 5 stars   
26  Wireless Earbuds SOUNDPEATS Sonic in-Ear Wirel...  3.9 out of 5 stars   
27  SAMSUNG Galaxy Buds Pro, True Wireless Earbuds...  4.2 out of 5 stars   
28  Lenovo Earphone Bluetooth5.0 Wireless Headset ...  3.1 out of 5 stars   
29  Sony MDR-ZX110AP Wired On-Ear Headphones with ...  4.1 out of 5 stars   
30  Sony WF-C500 True Wireless Headphones - Up to ...  5.0 out of 5 stars   
31  Wired Lightning Headset Earphone for Apple iPh...  2.0 out of 5 stars   
32  Samsung Galaxy SM-R175 Wireless Buds Plus with...  4.2 out of 5 stars   
33  HyperX Cloud II Gaming Headset for PC & PS4 & ...  4.6 out of 5 stars   
34  HUAWEI FreeBuds Pro Bluetooth Wireless Earphon...  4.4 out of 5 stars   
35          Nokia Lite Earbuds BH-205 - Black, Normal  3.2 out of 5 stars   
36  True Wireless Earbuds, Oraimo Bluetooth 5.2 He...                 NaN   
37  JBL TUNE115TWS True Wireless Earbuds Black, small  4.0 out of 5 stars   
38  Wireless Earbuds SoundPEATS TrueAir2 Bluetooth...  3.8 out of 5 stars   
39  Wireless Earbuds SoundPEATS T2 Hybrid Active N...  4.2 out of 5 stars   
40  HUAWEI FreeBuds Studio Wireless Earphones, Int...  4.8 out of 5 stars   
41  True Wireless Earphones, Bluetooth 5 earbuds w...  4.3 out of 5 stars   
42  AirPods Case Protective Silicone Cover with Ca...  3.9 out of 5 stars   
43  HUAWEI BLUETOOTH HEADPHONE LITE AM61 MOONLIGHT...  4.3 out of 5 stars   
44  SoundPEATS H1 Wireless Earbuds, Bluetooth V5.2...  4.0 out of 5 stars   
45  For iPhone X 8 7 Plus Bluetooth Earphones Wire...  2.5 out of 5 stars   
46  Wireless Earbuds, SOUNDPEATS Q Bluetooth 5.0 H...  4.1 out of 5 stars   
47  Joyroom JR-T03S In-Ear Detection True Wireless...  2.8 out of 5 stars   
48  Sony WH-CH510 Wireless Bluetooth On-Ear with M...  3.6 out of 5 stars   
49  Anker Soundcore Life P2 Mini Bluetooth Earphon...  4.2 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.1      2,777           

# Best Sellers in Headphones, Earbuds & Accessories (Page 2 )

In [98]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966390031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [99]:
response = requests.get(url)
response.status_code

200

In [100]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [101]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [102]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [103]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.2 out of 5 stars\n'

In [104]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [105]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Wireless Earbuds, SoundPEATS T3 Active Noise Canceling with AI ENC, Bluetooth 5.2 in-Ear Headphones, ANC Earbuds for Clear Calls, Transparency Mode, Touch Control, Total 16.5 Hrs
4.4 out of 5 stars
4.4
68
68
SAR 127.20
127.20


In [106]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [107]:
products_df10 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df10

pro_name            pro_rate  \
0   Wireless Earbuds, SoundPEATS T3 Active Noise C...  4.4 out of 5 stars   
1   Bluetooth Earphones, SoundPEATS Dual Dynamic D...  4.2 out of 5 stars   
2   SKULLCANDY Dime True Wireless In-Ear Earbuds W...  4.1 out of 5 stars   
3   Sony WH-1000XM4 Wireless Noise Cancelling Blue...  4.5 out of 5 stars   
4   Datazone Ear phone Headphones,crystal clear so...  3.6 out of 5 stars   
5   Amoi F9 Bluetooth 5.0 Wireless Earbuds,IPX7 Wa...  2.8 out of 5 stars   
6   G9000 Stereo Gaming Headset for PS4, PC, Xbox ...  3.5 out of 5 stars   
7   Huawei Honor xsport Bluetooth Headset am61 IPX...  2.7 out of 5 stars   
8       TOSHIBA RZE-BT1200H Wireless Headphones Black  4.5 out of 5 stars   
9   Wireless Earbuds, Bluetooth 5.2 True Wireless ...  3.5 out of 5 stars   
10          JBL In-Ear Headphones, RED - T110, Normal  4.2 out of 5 stars   
11  Silicone Case for AirPods Pro, Protective Shoc...  3.9 out of 5 stars   
12             Astro A10 Headset Wired For PS4, Black  4.4 out of 5 stars   
13  Gaming Headset for PS4, Xbox One, PC, Laptop, ...  4.3 out of 5 stars   
14  SAMSUNG Galaxy Buds2 Earbuds with Charging Cas...  4.2 out of 5 stars   
15  ElloGear 2020 Earbuds Stereo Headphones for Sa...  4.0 out of 5 stars   
16  Joyroom JR-T03S TWS Bluetooth True Wireless St...  2.7 out of 5 stars   
17  JBL T510 WIRELESS ON-EAR HEADPHONE WITH MIC - ...  4.6 out of 5 stars   
18  Jabra Elite 75t Earbuds – Active Noise Cancell...  4.3 out of 5 stars   
19  JBL TUNE 700BT WIRELESS OVER-EAR HEADPHONE - B...  4.0 out of 5 stars   
20  UGREEN USB C to 3.5mm Headphone Jack Audio Cha...  4.1 out of 5 stars   
21  Anker Soundcore Liberty Air 2 Pro True Wireles...  4.1 out of 5 stars   
22  Bose QuietComfort Earbuds - True Wireless Nois...  4.4 out of 5 stars   
23  ION AirPods Pro Active Noise Cancelling Wirele...  1.8 out of 5 stars   
24  SoundPEATS True Wireless Bluetooth Earbuds in-...  5.0 out of 5 stars   
25  Bose Noise Cancelling Wireless Bluetooth Headp...  4.5 out of 5 stars   
26  F9-5B TWS Earphone with Power Bank Hifi True S...  3.5 out of 5 stars   
27  Beats Studio Buds True Wireless Noise Cancelli...  3.5 out of 5 stars   
28  AccLoo Wireless Earbuds Bluetooth 5.0 Headphon...  3.9 out of 5 stars   
29  Anker Soundcore Liberty Air 2 Pro True Wireles...  4.1 out of 5 stars   
30  JOYROOM JR-T03s white Wireless bluetooth headp...  2.7 out of 5 stars   
31  Huawei Stereo Earphones with Remote and Microp...  4.1 out of 5 stars   
32  UGREEN USB-C to 3.5mm Adapter Full Compatibili...  4.2 out of 5 stars   
33  Wireless Earbuds SoundPEATS 100Hours Playtime ...  4.0 out of 5 stars   
34  Sony WH-CH510 Wireless Bluetooth On-Ear with M...  3.6 out of 5 stars   
35  Bluetooth Headphones, SoundPEATS A6 Hybrid Act...  4.2 out of 5 stars   
36  beats Flex – All-Day Wireless Earphones – beat...  3.4 out of 5 stars   
37  SoundPEATS TrueFree2 Wireless Earbuds Bluetoot...  4.0 out of 5 stars   
38  Display Headphone Stand Headset Holder Earphon...  4.3 out of 5 stars   
39  Belkin Lightning In-Ear Earbud for iPhones Bla...  3.9 out of 5 stars   
40             SAMSUNG 870 QVO 2TB 2.5" MZ-77Q2T0B/AM  4.8 out of 5 stars   
41                    JBL T110 In Ear Headphone, Blue  4.2 out of 5 stars   
42  AirPods Case Protective Silicone Cover with Ca...  3.9 out of 5 stars   
43  Sony WF-1000XM3 True Wireless Noise Cancelling...  3.8 out of 5 stars   
44  HUAWEI FreeBuds 4i Wireless In-Ear Bluetooth E...  4.4 out of 5 stars   
45  Razer Kraken - Wired Gaming Headset for Multip...  4.4 out of 5 stars   
46  Airpods Pro Case, Shockproof Scratch Resistant...  4.3 out of 5 stars   
47  Bluetooth 5.0 Headphones with Flip-to-Mute Mic...  4.5 out of 5 stars   
48  Razer Hammerhead True Wireless - Wireless Earb...  4.0 out of 5 stars   
49  Ear Pad Replacement Soft Memory Foam Replaceme...  3.3 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.4         68           

# Best Sellers in Mobile Phones & Communication Products (Page 1 )

In [108]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966387031/ref=zg_bs_nav_1_electronics"

In [109]:
response = requests.get(url)
response.status_code

200

In [110]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [111]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [112]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [113]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n1.0 out of 5 stars\n'

In [114]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [115]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB, 4GB RAM, LTE, Black (KSA Version)
3.0 out of 5 stars
3.0
2
2
SAR 539.00
539.00


In [116]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [117]:
products_df11 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df11

pro_name            pro_rate  \
0   SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB,...  3.0 out of 5 stars   
1   Samsung Galaxy A12 LTE Dual SIM Smartphone - 6...  1.0 out of 5 stars   
2                Apple 20W USB-C Power Adapter, White  4.5 out of 5 stars   
3   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.1 out of 5 stars   
4                    Apple AirPods with Charging Case  4.1 out of 5 stars   
5   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.5 out of 5 stars   
6   Anker PowerCore Select 20000, 20000mAh Power B...  4.1 out of 5 stars   
7   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.2 out of 5 stars   
8   Apple Watch Series 6 (GPS, 44mm) - Space Grey ...  4.6 out of 5 stars   
9                               New Apple Airpods Pro  4.3 out of 5 stars   
10  Apple iPhone 12 Pro With FaceTime (256GB) - Pa...  4.2 out of 5 stars   
11  JBL Flip 5 Portable Speaker Waterproof Wireles...  4.6 out of 5 stars   
12  Sony WH-1000XM4 Wireless Noise Cancelling Blue...  4.4 out of 5 stars   
13  Apple iPhone 12 Pro With FaceTime (128GB) - Pa...  4.2 out of 5 stars   
14       Apple iPhone 12 With FaceTime (128GB) - Blue  4.4 out of 5 stars   
15  Apple iPhone 12 Pro Max With FaceTime (128GB) ...  4.4 out of 5 stars   
16  SoundPEATS Air3 Wireless Earbuds Mini Bluetoot...  4.0 out of 5 stars   
17                 JBL In-Ear Headphones, Black, T110  4.2 out of 5 stars   
18  Sony WI-C200 Wireless In-ear Bluetooth Headpho...  3.7 out of 5 stars   
19  Xiaomi Redmi 9A Dual SIM, 32GB, 2GB RAM, 4G LT...  4.0 out of 5 stars   
20  Wireless Earbuds SoundPEATS TrueAir2 Bluetooth...  3.8 out of 5 stars   
21   New Apple iPhone 13 with FaceTime (256GB) - Blue  4.3 out of 5 stars   
22  Anker Soundcore Life Q30 Bluetooth Headphones,...  4.6 out of 5 stars   
23  Apple Watch Series 6 (GPS, 44mm) - Blue Alumin...  4.6 out of 5 stars   
24  Samsung Galaxy S21 5G | Pro Grade Triple Camer...  3.6 out of 5 stars   
25      Apple iPhone 12 With FaceTime (128GB) - White  4.4 out of 5 stars   
26  Apple Watch Series 6 (GPS, 40mm) - Gold Alumin...  4.6 out of 5 stars   
27                 New Apple AirPods (3rd generation)  4.3 out of 5 stars   
28     Apple iPhone 12 With FaceTime (256GB) - Purple  4.4 out of 5 stars   
29  Anker PowerLine III USB-C to USB-C Cable USB-C...  5.0 out of 5 stars   
30  Xiaomi Redmi Note 10S, Dual SIM, 128GB, 6GB RA...  3.8 out of 5 stars   
31  Anker Nano iPhone Charger, 20W PIQ 3.0 Durable...  4.2 out of 5 stars   
32  Anker USB C to Lightning Cable (6 ft), Powerli...  4.0 out of 5 stars   
33  Bluetooth Wireless Headphones 40 Hours Playtim...  4.2 out of 5 stars   
34  Samsung Galaxy S21 Ultra 5G Android Smartphone...  3.8 out of 5 stars   
35  Samsung Galaxy S20 FE Dual SIM - 128GB, 8GB RA...  4.1 out of 5 stars   
36  Apple iPhone 12 Pro Max With FaceTime (256GB) ...  4.4 out of 5 stars   
37  Samsung Galaxy S20 FE 4G Android Smartphone, 1...                 NaN   
38  SanDisk Ultra Micro SD Card Android - Class 10...  4.4 out of 5 stars   
39  UGREEN USB C Cable 2M, Braided 100W Power Deli...  4.2 out of 5 stars   
40  Apple iPhone 12 Pro Max With FaceTime (128GB) ...  4.4 out of 5 stars   
41  Sony MDR-ZX110AP Extra Bass Smartphone Headset...  4.1 out of 5 stars   
42  Anker PowerCore III 10K, Wireless Portable Cha...  4.7 out of 5 stars   
43  UGREEN 2 Pack Screen Protector for iPhone 13/1...  4.4 out of 5 stars   
44                                  Apple AirPods Pro  4.3 out of 5 stars   
45  Stylus Pen for iPad with Palm Rejection，Active...  2.7 out of 5 stars   
46  Compatible with Apple Watch Case Series 4 Seri...  3.9 out of 5 stars   
47  Samsung Galaxy Note20 5G, Pro Grade Triple Cam...  4.1 out of 5 stars   
48        Apple iPhone 12 With FaceTime (64GB) - Blue  4.4 out of 5 stars   
49  Anker 30W PIQ 3.0 USB-C Fast Charger Adapter, ...  4.5 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             3.0          2           

# Best Sellers in Mobile Phones & Communication Products (Page 2 )

In [118]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966387031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [119]:
response = requests.get(url)
response.status_code

200

In [120]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [121]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [122]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [123]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.3 out of 5 stars\n'

In [124]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [125]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

UGREEN Fast Car Charger Adapter 42.5W Dual USB Quick Charge QC 3.0 and PD Fast Charging Car Plug for iPhone 13 Pro/13 Pro Max/13/13 mini/12 Pro Max/11Pro Max,New iPad 9,iPad mini 6,Galaxy S20 S10,etc
4.3 out of 5 stars
4.3
2,191
2191
SAR 63.20
63.20


In [126]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [127]:
products_df12 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df12

pro_name            pro_rate  \
0   UGREEN Fast Car Charger Adapter 42.5W Dual USB...  4.3 out of 5 stars   
1   ELON Fast Charging Cable for iPhone USB to Lig...  4.3 out of 5 stars   
2   UGREEN PD 20W Car Charger Fast Charging for iP...  4.3 out of 5 stars   
3   Samsung Galaxy M11 Dual SIM - 32GB, 3GB RAM, 4...  4.0 out of 5 stars   
4   Xiaomi POCO X3 Pro, Dual SIM, 256GB, 8GB RAM, ...  4.2 out of 5 stars   
5   Anker 30W PIQ 3.0 USB-C Fast Charger Adapter, ...  4.5 out of 5 stars   
6   SoundPEATS Smart Watch New Upgraded 13 Sports ...  4.1 out of 5 stars   
7   HUAWEI FreeBuds 4i Wireless In-Ear Bluetooth E...  4.1 out of 5 stars   
8   UGREEN iPhone Charger PD20W USB C iPhone 13 Fa...  4.2 out of 5 stars   
9      Apple iPhone 12 With FaceTime (128GB) - Purple  4.4 out of 5 stars   
10  JBL CLIP4 WIRELESS PORTABLE SPEAKER - Blue/Pin...  4.7 out of 5 stars   
11  Samsung Galaxy A72 | Ultra High-Res Quad Camer...  4.2 out of 5 stars   
12  Wireless Earbuds, SOUNDPEATS S5 Over-Ear Hooks...  4.4 out of 5 stars   
13   New Apple iPhone 13 with FaceTime (128GB) - Blue  4.3 out of 5 stars   
14  Apple iPhone 12 Pro With FaceTime (256GB) - Si...  4.2 out of 5 stars   
15  UGREEN Car Phone Mount Dashboard Car Holder Wi...  4.4 out of 5 stars   
16  UGREEN Magnetic Car Phone Holder Air Vent Moun...  4.0 out of 5 stars   
17  UGREEN iPhone Protective Case Compatible for i...  4.5 out of 5 stars   
18  Samsung Galaxy S21 Dual SIM - 128GB, 8GB RAM, ...  3.6 out of 5 stars   
19  UGREEN USB C Cable 3A Fast Charging Cable Nylo...  4.3 out of 5 stars   
20  ibsun Wireless Charger, 3 in 1 Wireless Chargi...  4.1 out of 5 stars   
21  JBL T110 Wired Universal In-Ear Headphone with...  4.2 out of 5 stars   
22  UGREEN iPhone Lightning Cable 2M [MFi Certifie...  4.6 out of 5 stars   
23  UGREEN iPhone 13 Charger Cable [MFi Certified]...  4.1 out of 5 stars   
24                    Apple iPhone 11 (128GB) - Green  4.3 out of 5 stars   
25  Wireless Earbuds True Wireless Bluetooth Earph...  4.0 out of 5 stars   
26  Samsung Galaxy Note20 5G, Pro Grade Triple Cam...  4.1 out of 5 stars   
27  Milanese Loop Bracelet Stainless Steel band Fo...  4.3 out of 5 stars   
28  UGREEN 65W USB C Charger Plug 4 Port GaN Type ...  4.2 out of 5 stars   
29  2Pack Apple Original Charger [Apple MFi Certif...  4.5 out of 5 stars   
30  Bose Noise Cancelling Wireless Bluetooth Headp...  4.5 out of 5 stars   
31  Bose QuietComfort Earbuds - True Wireless Nois...  4.4 out of 5 stars   
32  Hybrid Active Noise Cancelling Headphones with...  4.8 out of 5 stars   
33  Long ARM Black Color Flexible Clip Lazy Bed De...  3.4 out of 5 stars   
34  UGREEN USB C Cable 3A Fast Charging Cable Nylo...  4.3 out of 5 stars   
35  iPhone Charger Lightning Cable 10ft - by TalkW...  4.1 out of 5 stars   
36  Samsung Galaxy S21 Ultra 5G Android Smartphone...  3.8 out of 5 stars   
37  Bose Noise Cancelling Wireless Bluetooth Headp...  4.5 out of 5 stars   
38  Apple Watch Series 6 (GPS, 40mm) - Space Grey ...  4.6 out of 5 stars   
39  UGREEN USB C Cable USB A to Type C Data Cable ...  4.4 out of 5 stars   
40         Anker Powerline+ II 6 Foot Lightning Cable  4.1 out of 5 stars   
41  HUAWEI HW-TIA-B09-BLACK WATCH FIT Smartwatch w...  4.5 out of 5 stars   
42  New Apple iPhone 13 Pro with FaceTime (256GB) ...  4.2 out of 5 stars   
43      Apple iPhone 12 With FaceTime (128GB) - Black  4.4 out of 5 stars   
44  Samsung Galaxy A02 Dual SIM Smartphone - 32GB,...  3.6 out of 5 stars   
45    Apple Lightning to 3.5mm Headphone Jack Adapter  4.2 out of 5 stars   
46  Apple Watch Series 6 (GPS, 40mm) - Blue Alumin...  4.6 out of 5 stars   
47  SanDisk Ultra microSDXC 128GB 100MB/s Class 10...  4.4 out of 5 stars   
48  UGREEN iPhone Protective Case Compatible for i...  4.7 out of 5 stars   
49  Samsung EP-TA800 Travel Adapter for Super Fast...  4.3 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.3      2,191           

# Best Sellers in Wearable Technology (Page 1)

In [128]:
url= "https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966397031/ref=zg_bs_pg_1?ie=UTF8&pg=1"

In [129]:
response = requests.get(url)
response.status_code

200

In [130]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [131]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [132]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [133]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.6 out of 5 stars\n'

In [134]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [135]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Apple Watch Series 6 (GPS, 44mm) - Space Grey Aluminium Case with Black Sport Band
4.6 out of 5 stars
4.6
306
306
SAR 1,349.00
1349.00


In [136]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [137]:
products_df13 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df13

pro_name            pro_rate  \
0   Apple Watch Series 6 (GPS, 44mm) - Space Grey ...  4.6 out of 5 stars   
1   Apple Watch Series 6 (GPS, 44mm) - Blue Alumin...  4.6 out of 5 stars   
2   Apple Watch Series 6 (GPS, 40mm) - Gold Alumin...  4.6 out of 5 stars   
3   Compatible with Apple Watch Case Series 4 Seri...  3.9 out of 5 stars   
4   HUAWEI Band 6, All-day SpO2 Monitoring, 1.47" ...  4.4 out of 5 stars   
5   SoundPEATS Smart Watch New Upgraded 13 Sports ...  4.1 out of 5 stars   
6   ibsun Wireless Charger, 3 in 1 Wireless Chargi...  4.1 out of 5 stars   
7   Milanese Loop Bracelet Stainless Steel band Fo...  4.3 out of 5 stars   
8   Apple Watch Series 6 (GPS, 40mm) - Space Grey ...  4.6 out of 5 stars   
9   HUAWEI HW-TIA-B09-BLACK WATCH FIT Smartwatch w...  4.5 out of 5 stars   
10  Apple Watch Series 6 (GPS, 40mm) - Blue Alumin...  4.6 out of 5 stars   
11                      Fitbit-Inspire 2, Black/Black  4.5 out of 5 stars   
12  Fitbit Ace 3, Activity Tracker for Kids 6+ wit...  4.4 out of 5 stars   
13  Xiaomi Band 5 Smart Fitness Bracelet Heart Rat...  4.5 out of 5 stars   
14  Apple Watch Series 7 (GPS, 41mm) - Midnight Al...  5.0 out of 5 stars   
15  Smart Watch, YCCORG Fitness Tracker with Heart...  3.8 out of 5 stars   
16  SKULLCANDY Dime True Wireless In-Ear Earbuds W...  4.1 out of 5 stars   
17  Fitbit Versa 3, Health & Fitness Smartwatch wi...  4.4 out of 5 stars   
18                     Fitbit Charge 5,Graphite/Black  3.1 out of 5 stars   
19  Xioami Mi Smart Band 6 Sports Smart Bracelet- ...  4.3 out of 5 stars   
20  24HOCL Smart Watch for Kids Girls Boys, Activi...  5.0 out of 5 stars   
21          Apple Watch Magnetic Charging Cable (1 m)  3.0 out of 5 stars   
22  hw22 plus Smart Watch series 6 Bluetooth Call ...  2.4 out of 5 stars   
23  24HOCL Smart Watch Fitness Tracker with Temper...  4.1 out of 5 stars   
24  Huawei Watch GT 2 Pro Glass Screen Protector, ...  3.0 out of 5 stars   
25  Apple Watch Series 7 (GPS, 45mm) - Midnight Al...  4.6 out of 5 stars   
26  Fitbit Sense, Advanced Smartwatch with Tools f...  4.2 out of 5 stars   
27  Xiaomi Mi Band 4 Smart Bluetooth Fitness Brace...  4.4 out of 5 stars   
28  Samsung Galaxy Watch3 Stainless BT 45mm, Black...  4.3 out of 5 stars   
29  OMIRA Smart Watch, Fitness Tracker with Heart ...  3.8 out of 5 stars   
30  Smart Watch for Women, AGPTEK 1.69"(43mm) Smar...  3.7 out of 5 stars   
31  INFOSUN Compatible with Apple Watch Bands 42mm...  3.5 out of 5 stars   
32  HONOR Band 6, Model ARG-B39, 1.47" AMOLED Disp...  4.1 out of 5 stars   
33  HUAWEI WATCH FIT Elegant Smartwatch, Stainless...  4.0 out of 5 stars   
34  Apple Watch Series 6 (GPS, 40mm) - Silver Alum...  4.6 out of 5 stars   
35  Compatible with Apple Watch Band 40mm 38mm, Ad...  3.8 out of 5 stars   
36  Apple Watch SE (GPS, 44mm) - Silver Aluminium ...  4.4 out of 5 stars   
37  Case for Apple Watch 7 45mm Soft Slim TPU All ...  3.0 out of 5 stars   
38  HUAWEI Talkband B6 Smart Band, Fitness Activit...  5.0 out of 5 stars   
39  Apple Watch Series 7 (GPS + Cellular, 45mm) - ...  5.0 out of 5 stars   
40  Smart Watch Men HW22 Pro Series 6 Sport Blueto...  4.5 out of 5 stars   
41  24HOCL Smart Watch with 1.69'' Full Touch Scre...  4.1 out of 5 stars   
42  Compatible For Apple Watch Band 42/44mm 38/40m...  4.0 out of 5 stars   
43  Smart Watch for Men Women (Receive/Make Call)1...  1.8 out of 5 stars   
44  Smart Watch, Yccorg 1.54-inch Fitness Tracker ...  3.5 out of 5 stars   
45  Apple Watch Series 7 (GPS, 41mm) - Starlight A...  5.0 out of 5 stars   
46  Apple Watch Series 7 (GPS, 45mm) - Blue Alumin...                 NaN   
47  Xiaomi Mi Smart Watch Lite Black- 1.4 Inch Tou...  4.2 out of 5 stars   
48  Compatible with Apple Watch Band 45mm 44mm 42m...  4.1 out of 5 stars   
49  GEEAN Stainless Steel Watch Band for Apple Wat...  3.7 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.6        306           

# Best Sellers in Wearable Technology (Page 2)

In [138]:
url = "https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966397031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [139]:
response = requests.get(url)
response.status_code

200

In [140]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [141]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [142]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [143]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n3.2 out of 5 stars\n'

In [144]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [145]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Samsung Galaxy Watch Active 2 , 40 mm Aluminium, Pink Gold - SM-R830NZDAKSA
5.0 out of 5 stars
5.0
5
5




In [146]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [147]:
products_df14 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df14

pro_name            pro_rate  \
0   Samsung Galaxy Watch Active 2 , 40 mm Aluminiu...  5.0 out of 5 stars   
1   Screen Protector Compatible with Huawei Watch ...  3.2 out of 5 stars   
2   Compatible with Apple Watch Bands 38mm 40mm, A...  3.8 out of 5 stars   
3   Compatible with Apple Watch Band, Nylon Strap ...  5.0 out of 5 stars   
4   Lomet 22mm Stainless Steel Mesh Loop Bracelet ...  4.3 out of 5 stars   
5   Fitbit Versa 2 Health and Fitness Smartwatch -...  4.5 out of 5 stars   
6   SKULLCANDY Dime True Wireless In-Ear Earbuds W...  4.1 out of 5 stars   
7   Case Compatible for Huawei Watch FIT Screen Pr...  5.0 out of 5 stars   
8           Smart Watch 42mm Midnight Blue Sport Band  2.8 out of 5 stars   
9   HUAWEI WATCH FIT Elegant Smartwatch, Stainless...  4.7 out of 5 stars   
10  Apple Watch Series 7 (GPS + Cellular, 45mm) - ...                 NaN   
11  INFOSUN Compatible with Apple Watch Bands 42mm...  3.5 out of 5 stars   
12  INFOSUN Compatible with Apple Watch Bands 42mm...  3.5 out of 5 stars   
13  Apple Watch Series 7 (GPS, 41mm) - (PRODUCT)RE...  5.0 out of 5 stars   
14  Fitbit Sense, Advanced Smartwatch with Tools f...  4.2 out of 5 stars   
15  Pebble Pace Smart Watch with Full Touch Dynami...  3.9 out of 5 stars   
16  Fitbit Versa 2 Special Edition Health and Fitn...  4.5 out of 5 stars   
17  Fire-Boltt SpO2 Full Touch 1.4 inch Smart Watc...  4.1 out of 5 stars   
18  SKULLCANDY Dime True Wireless In-Ear Earbuds W...  4.1 out of 5 stars   
19  MAZTRON 6-Pack Silicone Band Compatible with A...  4.4 out of 5 stars   
20  HW22 PRO MAX Smart watch 1.78 Inch IPS Color S...  3.5 out of 5 stars   
21  Smárt Watches - HW22 Plus Smárt Watch Women 1....  3.7 out of 5 stars   
22  Apple Watch Series 7 (GPS, 45mm) - Green Alumi...  5.0 out of 5 stars   
23  Screen Protector Compatible with Huawei Watch ...  3.2 out of 5 stars   
24  Compatible with Apple Watch Band 38mm 40mm, Ad...  3.8 out of 5 stars   
25  Smart Watch Rubber Band For Android & iOS,Blue...                 NaN   
26  GEEAN Stainless Steel Watch Band Metal Strap f...  4.1 out of 5 stars   
27  Smart Watch, AGPTEK Smartwatch for Men Women I...  3.7 out of 5 stars   
28  (4-Pack) Spectre Shield Screen Protector for A...                 NaN   
29  Smart GSM Watch Phone Bluetooth touch screen -...  2.0 out of 5 stars   
30  20 Pieces Strap Replacement Compatible with Xi...  4.6 out of 5 stars   
31  Apple Watch Series 7 (GPS, 45mm) - Starlight A...  5.0 out of 5 stars   
32  Smart Watch,Fitness Watch Cardio Exercise Hear...  5.0 out of 5 stars   
33        Apple AirTag Leather Key Ring - Baltic Blue                 NaN   
34  Compatible with Huawei Watch Fit Watch band , ...  3.5 out of 5 stars   
35     Garmin Solar-Powered Rugged Outdoor Smartwatch  4.7 out of 5 stars   
36  Barton Canvas Watch Bands - Stainless Steel Ha...  4.3 out of 5 stars   
37  HW22 PRO MAX MYK Smart watch 1.78LTPS full Scr...                 NaN   
38  INFOSUN Compatible with Apple Watch Bands 38mm...  3.5 out of 5 stars   
39  Adjustable Woven replacement bands Compatible ...  4.0 out of 5 stars   
40    SMART WATCH series 6 space aluminum case (Pink)  2.4 out of 5 stars   
41  M4 Bluetooth Smart Watch Bracelet Wristband wi...  2.2 out of 5 stars   
42  GEEAN Stainless Steel Watch Band Metal Strap f...  4.1 out of 5 stars   
43  w26 plus smart watch w26 smart watch w26 smart...  3.1 out of 5 stars   
44  Apple Watch Leather Link (45mm) - Golden Brown...                 NaN   
45  Fitbit Versa 2 Health and Fitness Smartwatch -...  4.6 out of 5 stars   
46  INFOSUN Compatible with Apple Watch Bands 38mm...  3.5 out of 5 stars   
47  Elite Strap for Oculus Quest 2, Adjustable Hal...  4.1 out of 5 stars   
48  Tycom Case Compatible with Apple Watch Series ...  4.5 out of 5 stars   
49  Apple Watch Series 6 (GPS, 44mm) - Gold Alumin...  4.6 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             5.0          5           

# Best Sellers in Car & Vehicle Electronics (Page 1)

In [148]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966386031/ref=zg_bs_nav_1_electronics"

In [149]:
response = requests.get(url)
response.status_code

200

In [150]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [151]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [152]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [153]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.3 out of 5 stars\n'

In [154]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [155]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

UGREEN Fast Car Charger Adapter 42.5W Dual USB Quick Charge QC 3.0 and PD Fast Charging Car Plug for iPhone 13 Pro/13 Pro Max/13/13 mini/12 Pro Max/11Pro Max,New iPad 9,iPad mini 6,Galaxy S20 S10,etc
4.3 out of 5 stars
4.3
2,191
2191
SAR 63.20
63.20


In [156]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [157]:
products_df15 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df15

pro_name            pro_rate  \
0   UGREEN Fast Car Charger Adapter 42.5W Dual USB...  4.3 out of 5 stars   
1   UGREEN PD 20W Car Charger Fast Charging for iP...  4.3 out of 5 stars   
2   UGREEN Car Phone Mount Dashboard Car Holder Wi...  4.4 out of 5 stars   
3   UGREEN Magnetic Car Phone Holder Air Vent Moun...  4.0 out of 5 stars   
4   UGREEN Bluetooth Aux Adapter, Bluetooth 5.0 Au...  4.5 out of 5 stars   
5   Muson Car Phone Mount, Dashboard/Air Vent/Wind...  3.7 out of 5 stars   
6   UGREEN Car Air Vent Mount Cell Phone Holder Gr...  4.4 out of 5 stars   
7   Magnetic Phone Car Mount, WORLDMOM Strong Magn...                 NaN   
8   UGREEN Car Phone Holder Magnetic Dashboard Mob...  4.2 out of 5 stars   
9   UGREEN Car Phone Holder Air Vent Cell Phone Mo...  4.3 out of 5 stars   
10  UGREEN Bluetooth 5.0 Adapter Car Bluetooth V5....  4.2 out of 5 stars   
11          Belkin Magnetic Car Vent Mount V2 MagSafe  3.7 out of 5 stars   
12  UGREEN Magnetic Car Mount Dashboard Cell Phone...  4.1 out of 5 stars   
13  UGREEN Fast Car Charger 36W Dual USB QC 3.0 Qu...  4.3 out of 5 stars   
14  15W Qi Wireless Fast Car Mount Charger, Auto D...  4.4 out of 5 stars   
15  UGREEN Car Air Vent Mount Cell Phone Holder Gr...  4.4 out of 5 stars   
16  UGREEN Magnetic Car Mount Phone Holder Univers...  4.2 out of 5 stars   
17  Anker Power Drive 2 24W 2 Port Car Charger For...  4.2 out of 5 stars   
18                        ANKER POWERDRIVE 2 QC BLACK  3.9 out of 5 stars   
19  AccLoo Wireless Car Charger, 15W Qi Fast Charg...  5.0 out of 5 stars   
20  UGREEN Bluetooth FM Transmitter USB Car Fast C...  3.7 out of 5 stars   
21  Go-Des Mini Strip Car Mount, Universal Mobile ...  4.5 out of 5 stars   
22  Tekpatt Car Phone Holder, Universal Air Vent C...  3.5 out of 5 stars   
23  UGREEN Bluetooth 5.0 Audio Transceiver Wireles...  3.8 out of 5 stars   
24  UGREEN Fast Car Charger Set with USB C Cable Q...  4.4 out of 5 stars   
25  Baseus 360-degree Rotation Magnetic Mount Hold...  3.8 out of 5 stars   
26  Car Phone Mount, Air Vent Cell Phone Holder fo...  4.1 out of 5 stars   
27  UGREEN Bluetooth Receiver for Car, Portable Wi...  4.0 out of 5 stars   
28  Belkin USB-C PD Car Charger 36W (Dual 18W USB-...  4.6 out of 5 stars   
29  Bluetooth V2.0 7 Inch 2 DIN Car Video Stereo P...  3.1 out of 5 stars   
30  UGREEN Car Phone Mount CD Slot Holder Gravity ...  4.0 out of 5 stars   
31  Huawei CP37 Type-C Car Charger with Super Char...  4.7 out of 5 stars   
32  UGREEN Bluetooth Aux Adapter Bluetooth Car Rec...  4.4 out of 5 stars   
33  Tekpatt Car Phone Holder, Universal Air Vent C...  5.0 out of 5 stars   
34  UGREEN Dashboard Phone Holder 360 Degree Car P...  3.6 out of 5 stars   
35  UGREEN Car Phone Holder for CD Slot Auto Lock ...  4.1 out of 5 stars   
36  Promate Magnetic Car Mount Holder, Flexible Go...  4.5 out of 5 stars   
37  UGREEN Bike Phone Holder, Bicycle Motorcycle P...  4.3 out of 5 stars   
38  UGREEN Dashboard Car Phone Clip Holder Dash HU...  3.9 out of 5 stars   
39  70mai A500S Pro Plus+, 2K Front and Interior, ...                 NaN   
40  USB C Car Charger, Anker 33W PowerDrive PD＋ 2 ...  4.6 out of 5 stars   
41  SOOBA KN318 BT 5.1 Audio Receiver Adapter 3.5m...                 NaN   
42  Bluetooth 5.0 Transmitter 2 in 1 Bluetooth Rec...  5.0 out of 5 stars   
43  UGREEN Car Headrest Mount Car Phone Mount Mobi...  4.1 out of 5 stars   
44  UGREEN Fast Car Charger PD 40W Dual USB C Port...  4.3 out of 5 stars   
45  UGREEN Car Phone Mount Dashboard Clip Cell Pho...  3.4 out of 5 stars   
46  360 Universal Flexible Lazy Bed Desktop Car St...  3.2 out of 5 stars   
47  SAMSUNG Super Fast Dual Car Charger (45W+15W) ...  4.7 out of 5 stars   
48  AccLoo Bluetooth FM Transmitter for Car,Blueto...  5.0 out of 5 stars   
49  CarlinKit Wired CarPlay Dongle Android Auto fo...  3.1 out of 5 stars   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             4.3      2,191             

# Best Sellers in Car & Vehicle Electronics (Page 2)

In [158]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966386031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [159]:
response = requests.get(url)
response.status_code

200

In [160]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [161]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [162]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [163]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n5.0 out of 5 stars\n'

In [164]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [165]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Car Phone Mount, PHOCAR Universal Phone Holder for Car, Dashboard Cell Phone Stand Compatible with iPhone 12 pro max, LG, Samsung
2.8 out of 5 stars
2.8
6
6
SAR 29.99
29.99


In [166]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [167]:
products_df16 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df16

pro_name            pro_rate  \
0   Car Phone Mount, PHOCAR Universal Phone Holder...  2.8 out of 5 stars   
1   4 Types 12V Add-a-Circuit Adapter & Fuse Kit -...  5.0 out of 5 stars   
2   LENCENT FM Transmitter, Bluetooth FM Transmitt...  4.4 out of 5 stars   
3   USB Charger Car Bluetooth 5.0 Fm Transmitter M...                 NaN   
4     Duracell Car Charger Single USB White - DR5020W  5.0 out of 5 stars   
5   Urise Car Phone Holder, 360° adjustable cup mo...  3.3 out of 5 stars   
6   iOttie Easy One Touch 5 Cup Holder Car Mount P...  4.4 out of 5 stars   
7   SUNJOYCO Car Cup Holder Phone Mount, Universal...  4.0 out of 5 stars   
8   UGREEN Car Charger, Dual USB 24W/4.8A All Meta...  4.4 out of 5 stars   
9   Aukey HD-C5 Car Mount Air Vent Magnetic Cell P...                 NaN   
10  Magnetic mobile holder - 360 dgree Rotation - ...  3.0 out of 5 stars   
11  USB C Car Charger Flush Cigarette Lighter Adap...  4.6 out of 5 stars   
12  Universal Adjustable Car Mount Stand for Smart...  3.8 out of 5 stars   
13  CASEON Car Vent Holder Phone Mount Universal s...  5.0 out of 5 stars   
14  120W USB C Car Fast Charger - Dual Ports PPS P...  3.0 out of 5 stars   
15  Replacement 4 Buttons Uncut Keyless Remote Key...  3.9 out of 5 stars   
16  Universal Smartphone Car Phone Holder Mount Cl...  3.0 out of 5 stars   
17  360° Rotation Car Phone Holder - This High Qua...  3.5 out of 5 stars   
18  ACDelco GM Original Equipment 214-1680 Vapor C...  4.7 out of 5 stars   
19  Tesa 51608 15 Original Wiring Loom Harness Adh...  4.7 out of 5 stars   
20  SMAPRO Car Phone Holder, Car Mount for All Sma...  3.2 out of 5 stars   
21  Belkin Boost Charge USB-C Fast Car Charger 20W...  4.5 out of 5 stars   
22  Yesido magic Glue Silicone Wall Cell Phone Sta...  4.8 out of 5 stars   
23  Baseus Small Ears Series Magnetic Bracket（Vert...  4.4 out of 5 stars   
24  360° Car Phone Holder Mount, Rotation Magnetic...                 NaN   
25  Car HUD Display, OBDⅡ+ Smart Gauge High Defini...  5.0 out of 5 stars   
26  EqiEch Bluetooth FM Transmitter for Car, Bluet...  5.0 out of 5 stars   
27  Cllena DIN Hella Plug to Quick Charge 3.0 USB ...  4.4 out of 5 stars   
28  Tekpatt Gravity Car Phone Holder, Universal Ai...  4.5 out of 5 stars   
29  Universal Dashboard Car Mount Holder Rearview ...  3.0 out of 5 stars   
30  FOOKANN Car Phone Holder Silver, 360 ° Rotatab...                 NaN   
31  GOMMLE Car Air Vent Mount, One-hand Operation ...  5.0 out of 5 stars   
32  (WIDSY) Automobile holders,phone mount,cup hol...  5.0 out of 5 stars   
33  UGREEN Mini Car Charger Quick Charge 24W Dual ...  4.5 out of 5 stars   
34  Music_90s RF Device Detector Hidden Camera Fin...                 NaN   
35  Bluetooth Car Kit AUX Music Receiver Handsfree...  3.7 out of 5 stars   
36  iPhone Car Charger, Anker 24W 4.8A 2-Port Ligh...  4.1 out of 5 stars   
37  Belkin BoostCharge Wireless Car Charger + Vent...  3.6 out of 5 stars   
38                        OBD 2 Wifi Car Error Reader  3.6 out of 5 stars   
39  GUB Bicycle & Motorcycle Phone Mount, Aluminum...  4.4 out of 5 stars   
40  360° Rearview Mirror Phone Holder, Universal C...  3.0 out of 5 stars   
41  iSportgo S30 Dash Cam Suction Mount with 10pcs...                 NaN   
42  SMAPRO Car and Desktop Phone Holder, Car Mount...  3.2 out of 5 stars   
43  Car Phone Mount Phone Holder for Car Dashboard...                 NaN   
44  Carlinkit Wireless USB Carplay Dongle Adapter ...  1.0 out of 5 stars   
45  Pawfly 20 Pack Double Sided Suction Cups 4/5 I...  3.9 out of 5 stars   
46  BoYaXiao 300 واط مجموعة الألواح الشمسية كاملة ...                 NaN   
47  Anker Mini 24W 4.8A Metal Dual USB Car Charger...                 NaN   
48  iOttie Easy One Touch 5 Dashboard & Windshield...  4.4 out of 5 stars   
49  Super Fast USB C Charger Kit, 25W PD&PPS EASDM...  5.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             2.8          6             

# Best Sellers in Electrical Power Accessories (Page 1)

In [168]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966395031/ref=zg_bs_nav_1_electronics"

In [169]:
response = requests.get(url)
response.status_code

200

In [170]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [171]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [172]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [173]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n3.9 out of 5 stars\n'

In [174]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [175]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Apple 20W USB-C Power Adapter, White
4.5 out of 5 stars
4.5
359
359
SAR 79.00
79.00


In [176]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [177]:
products_df17 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df17

pro_name            pro_rate  \
0                Apple 20W USB-C Power Adapter, White  4.5 out of 5 stars   
1   Extension Cord with 3 Power Socket and 3 USB S...  3.9 out of 5 stars   
2   FLIZIL Fast Charging Universal Travel Adapter,...  4.5 out of 5 stars   
3   Extension Cord with USB, Power Strip with 3 Ou...  3.7 out of 5 stars   
4   LDNIO SC3604 Socket extension, 6USB Ports 3.4A...  3.9 out of 5 stars   
5               Enriches electricity with 6 USB Ports  4.4 out of 5 stars   
6   Multi Extension Socket Plug Adapter with 3 USB...  4.5 out of 5 stars   
7   Belkin BSV804ar2M 8-Outlet Surge Protection Ex...  4.5 out of 5 stars   
8   Belkin BSV603ar2M 6 Way/6 Plug 2m Surge Protec...  4.5 out of 5 stars   
9   FLIZIL Power Strip Extension with 4 way Socket...  4.5 out of 5 stars   
10  FLIZIL Lightning Cable, Apple MFi Certified Li...  4.5 out of 5 stars   
11  Socket extension, 6USB Ports with on/off Switc...  3.0 out of 5 stars   
12  Universal AU US EU to UK AC Power Plug Travel ...  3.6 out of 5 stars   
13  BXOE - Extension Lead Tower 12 Way, Power Stri...  5.0 out of 5 stars   
14  Travel Adapter for KSA/UAE/UK, Plug for US/EU/...  4.4 out of 5 stars   
15  FLIZIL USB C Cable 3A Fast Charging Cable Nylo...  4.5 out of 5 stars   
16  Lawazim 2-Socket Extension Strip with 5 Meters...  3.7 out of 5 stars   
17  Double Socket Adapter with USB, 5V 2.1A USB Wa...  5.0 out of 5 stars   
18                          Socket Adapter 3 Way 7012  4.1 out of 5 stars   
19  Anself Intelligent Efficient Household 200W AC...  2.6 out of 5 stars   
20             TVON POWER SOCKET 5M W/2USB TN-U6603-5  3.7 out of 5 stars   
21  LDNIO POWERFUL CHARGING SERISE Power Strip wit...  3.7 out of 5 stars   
22  3-Socket Extension Cord with Individual on/off...  3.8 out of 5 stars   
23  5.6A Fast Charging Worldwide Travel Adapter Pl...  4.6 out of 5 stars   
24             Terminator 3 Way Universal Plug Socket  4.1 out of 5 stars   
25  3-Socket Extension Cord with Individual on/off...  3.8 out of 5 stars   
26  LM2596 DC-DC 3A Adjustable Buck Converter Elec...                 NaN   
27  Belkin BSV400ar2M 4 Way/4 Plug 2 m Surge Prote...  4.5 out of 5 stars   
28  HOOPO-Power Strip with 6 USB 3 Power Socket 5....  5.0 out of 5 stars   
29             4 Way Universal T-Socket Multi Adaptor  4.4 out of 5 stars   
30  Multi Plug Extension Sockets ，3 Way Multi Plug...                 NaN   
31  LENCENT Extension Lead with USB Slots, 4 Way O...  4.5 out of 5 stars   
32  Travel Adaptor for KSA/US/UK/JP/CN/AU Plug Con...  3.2 out of 5 stars   
33  Mark 3864 High Quality Power socket Extension 10m  2.6 out of 5 stars   
34  Moxom Power Strip with 4 Anti Static Sockets, ...  3.5 out of 5 stars   
35  LDNIO 4 Power Socket Extension 4 USB (18w) Def...  4.6 out of 5 stars   
36  Belkin BSV604ar2M 6 Way/ 6 Plug 2m Surge Prote...  4.5 out of 5 stars   
37  Black Extension Lead 4way Power Socket 1.8m Ex...  5.0 out of 5 stars   
38  PHLIGHT Vertical Power Strip 2 layers, 7 outle...  3.9 out of 5 stars   
39  Universal Travel Adapter, NTONPOWER Worldwide ...                 NaN   
40  US/CA/JP Type B Adaptor Plug with Flat Blades/...  3.4 out of 5 stars   
41  Extension Cord Tower Vertical Surge Protector ...  4.5 out of 5 stars   
42  iSONIC Power Socket Strip with 5 Outlets 2860W...                 NaN   
43  YUNSYE Power Strips Extension Lead w 6 USB Wal...  3.7 out of 5 stars   
44                  Power connection with 6 USB ports  3.3 out of 5 stars   
45  Belkin BSV401ar2M 4-Outlet Surge Protection Ex...  4.5 out of 5 stars   
46  Smart Power strip, Power extension 2 Way, 2 Qu...  5.0 out of 5 stars   
47  Extension Lead 2 Sockets Power Strip 1.8m Exte...  4.0 out of 5 stars   
48  Vike Voltage Converter, ABS Power Transformer ...  3.0 out of 5 stars   
49  Wall Mountable Extension Lead, NTONPOWER Trave...  4.7 out of 5 stars   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             4.5        359             

# Best Sellers in Electrical Power Accessories (Page 2)

In [178]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966395031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [179]:
response = requests.get(url)
response.status_code

200

In [180]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [181]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [182]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [183]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.4 out of 5 stars\n'

In [184]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [185]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

TOMSHOO Universal Travel Adapter 4 USB 2.4A Charger AC Power International Wall Charger
2.9 out of 5 stars
2.9
3
3
SAR 90.09
90.09


In [186]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [187]:
products_df18 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df18

pro_name            pro_rate  \
0   TOMSHOO Universal Travel Adapter 4 USB 2.4A Ch...  2.9 out of 5 stars   
1   Anker Universal Travel Adapter with 4 USB Port...  4.4 out of 5 stars   
2   Belkin SurgePlus USB Surge Protector, 2 USB 2....  4.8 out of 5 stars   
3   Vertical Power Strip 4 layers, 11 outlets with...  4.0 out of 5 stars   
4   Dual electrical outlet with triple and dual ou...                 NaN   
5   wafi World Travel Power adapter, all in one In...  4.0 out of 5 stars   
6   mini-head charger for Nokia phones compatible ...                 NaN   
7   KLARHEIT Upgraded Universal Travel Adapter One...  3.9 out of 5 stars   
8                         Apple 12W USB Power Adapter  4.5 out of 5 stars   
9   Vertical Power Strip 4 layers, 11 outlets with...  5.0 out of 5 stars   
10  LDNIO SC3412 Socket extension, 3USB Ports,Type...                 NaN   
11  Anker Extension Lead with 2 USB Ports and 4 Wa...  5.0 out of 5 stars   
12  Safemore Extension Cord Lead Electrical Surge ...  5.0 out of 5 stars   
13  Powerology 4 AC 3 USB & USB-C PD 35W Multiport...  4.0 out of 5 stars   
14  Universal Vertical Multi Socket 220V Electrica...                 NaN   
15  MIMCO 12VDC, 2 Ampere Power Adapter — AC100V-2...  4.4 out of 5 stars   
16  4 Layers Multi Plug With USB Port, Gray Vertic...                 NaN   
17                      DAEWOO 3 WAY UNIVERSAL SOCKET  5.0 out of 5 stars   
18  2 Pcs/Set Universal AC Power Plugs US To EU To...  3.6 out of 5 stars   
19  FLEXY® Germany 3-Way Surge Protected Extension...                 NaN   
20  Al Fanar 4-Socket Extension Cord (5m, CE045M0U...                 NaN   
21           Power connection of 2500 watts multi-use  4.0 out of 5 stars   
22  Travel Adapter for KSA/UAE/UK, Plug for US/EU/...  4.4 out of 5 stars   
23  Universal Power Adapter AC 100-240V DC 12V 2A ...  3.3 out of 5 stars   
24  Brennenstuhl Premium-Line 6-way Extension Sock...  3.6 out of 5 stars   
25          Extension Cord, 5 Meters, 4 Ports, German  4.9 out of 5 stars   
26  Electrical connection vertical format consists...  2.6 out of 5 stars   
27  USB Power Strip with Independent Switch, NTONP...                 NaN   
28  PHLIGHT Vertical Power Strip 3 layers, 11 outl...  3.7 out of 5 stars   
29  Universal Power Extension (902S) by Elexon ESM...  5.0 out of 5 stars   
30  GoolRC WiFi Smart Power Strip Socket Tuya App ...                 NaN   
31  Belkin BSV804 8 Way 2m Surge Protection Extens...  3.3 out of 5 stars   
32  Wall Mounted USB Power Strip, NTONPOWER Multi ...  4.2 out of 5 stars   
33  UK to EU AC Power Adapter Plug Adapter - Trave...  3.4 out of 5 stars   
34  PEGANT 4 Way 3M Power Extension Cord 4 Univers...  4.9 out of 5 stars   
35  LENCENT 2Pcs UK to EU Euro Europe Plug Adapter...                 NaN   
36  YUNSYE White UK 2 Pin To 3 Pin 1A Fuse Adaptor...  3.7 out of 5 stars   
37  LENCENT 2X EU to UK Plug Adapter, Europe Schuk...  5.0 out of 5 stars   
38  Key Power 200-Watt Step Down 220V to 110V Volt...  4.4 out of 5 stars   
39  Smart Power strip, Power extension 4 Way, 2 Qu...  3.8 out of 5 stars   
40  2-Socket Extension Cord with on/off Switch wit...  3.7 out of 5 stars   
41  [2-Pack]US USA America/ Canada/ EU Europe Euro...                 NaN   
42  Universal Vertical Extension Cord Lead Tower S...  4.4 out of 5 stars   
43                  Power Socket Extension Board Cord                 NaN   
44  Extension Power Cord Multi Plug Vertical Tower...  5.0 out of 5 stars   
45  Smart Power Strip Wi-Fi Smart Plug Socket Powe...  4.4 out of 5 stars   
46  10Pcs TP4056 5V 1A 18650 Lithium Battery Charg...                 NaN   
47  5pcs 3S BMS Module 12V 10A 18650 BMS Charger M...  4.0 out of 5 stars   
48  Onyehn 10Pcs 5V Boost Step Up Power Supply Mod...  4.6 out of 5 stars   
49  HWEN-JP Smart Power Extension WiFi Plug Surge ...  5.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             2.9          3             

# Best Sellers in Computer Tablets (Page 1)

In [188]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966433031/ref=zg_bs_nav_1_electronics"

In [189]:
response = requests.get(url)
response.status_code

200

In [190]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [191]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [192]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [193]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n3.2 out of 5 stars\n'

In [194]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [195]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

2021 Apple iPad Pro (11-inch, Wi-Fi, 128GB) - Space Grey (3rd Generation)
4.6 out of 5 stars
4.6
54
54
SAR 3,499.00
3499.00


In [196]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [197]:
products_df19 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df19

pro_name            pro_rate  \
0   2021 Apple iPad Pro (11-inch, Wi-Fi, 128GB) - ...  4.6 out of 5 stars   
1   SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
2   2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
3   Samsung Electronics A7 Tablet 10.4 Wi-Fi 64GB ...  4.1 out of 5 stars   
4   SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
5   2021 Apple 10.2-inch iPad (Wi-Fi, 64GB) - Spac...  4.2 out of 5 stars   
6   Lenovo Smart Tab M10 Plus, 10.3" Android Table...  4.2 out of 5 stars   
7   Samsung Galaxy Tab S7 Wi-Fi, Mystic Navy - 256 GB  4.7 out of 5 stars   
8   Samsung Galaxy Tab S7+ Wi-Fi, Mystic Black - 2...  4.7 out of 5 stars   
9   HUION HS64 Graphics Drawing Tablet with Batter...  4.4 out of 5 stars   
10  SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
11  Microsoft Surface GO 2 [STV-00005], Tablet-PC,...  4.5 out of 5 stars   
12    2021 Apple iPad mini (Wi-Fi, 64GB) - Space Grey  4.1 out of 5 stars   
13  Samsung Electronics Galaxy Tab S7 Wi-Fi, Mysti...  4.7 out of 5 stars   
14  Lenovo Tab P11 with Keyboard Pack and Precisio...  4.0 out of 5 stars   
15  2021 Apple iPad Pro (12.9-inch, Wi-Fi, 128GB) ...  4.9 out of 5 stars   
16  2021 Apple iPad Pro (11-inch, Wi-Fi, 256GB) - ...  4.6 out of 5 stars   
17  Samsung Galaxy Tab S7+ Wi-Fi, Mystic Black - 5...  4.7 out of 5 stars   
18  2021 Apple iPad Pro (12.9-inch, Wi-Fi, 512GB) ...  4.9 out of 5 stars   
19  2020 Apple iPad Air (10.9-inch, Wi-Fi, 256GB) ...  4.4 out of 5 stars   
20  Samsung Galaxy Tab S7 Wi-Fi, Mystic Black - 512GB  4.7 out of 5 stars   
21  Samsung Galaxy Tab S6 Lite 10.4", 64GB WiFi An...  4.3 out of 5 stars   
22  2021 Apple 10.2-inch iPad (Wi-Fi + Cellular, 6...  4.2 out of 5 stars   
23  AVITA Magus II 10.1" HD Tablet with Detachable...  4.0 out of 5 stars   
24  Lenovo Tab P11 (TB-J606L) 11 inch Tablet, Wi-F...  5.0 out of 5 stars   
25   2021 Apple iPad mini (Wi-Fi, 256GB) - Space Grey  4.1 out of 5 stars   
26  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
27  SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
28  Microsoft Surface Pro 7 Tablet - 12.3 Inch, 10...  4.6 out of 5 stars   
29  HUAWEI MatePad T 10 Kids Edition, 9.7’’ Tablet...                 NaN   
30  Samsung Electronics Tab A7 Lite 8.7" Gray 32GB...  3.5 out of 5 stars   
31  Samsung Galaxy Tab S7 FE Tablet - 64GB, 4GB RA...  2.0 out of 5 stars   
32  SAMSUNG Galaxy Tab S7 Wi-Fi, Mystic Silver - 2...  4.7 out of 5 stars   
33  Microsoft Surface Go 2 Tablet STQ-00005, Intel...  4.2 out of 5 stars   
34  Apple iPad Pro (11-inch, Wi-Fi, 1TB) - Space Grey  5.0 out of 5 stars   
35  2021 Apple 10.2-inch iPad (Wi-Fi, 256GB) - Spa...  4.2 out of 5 stars   
36  samsung galaxy tab s7 plus, 128 GB, 6 GB RAM, ...  4.5 out of 5 stars   
37  2021 Apple iPad Pro (11-inch, Wi-Fi, 512GB) - ...  4.6 out of 5 stars   
38  Huawei Matepad T10S, 10.1", WIFI, 32GB, Deepse...  3.1 out of 5 stars   
39  2021 Apple 10.2-inch iPad (Wi-Fi + Cellular, 6...  4.2 out of 5 stars   
40  Microsoft Surface Pro 7 Tablet - 12.3 Inch, 10...  4.5 out of 5 stars   
41  Microsoft Surface Pro 7 Tablet - 12.3 Inch, 10...  4.5 out of 5 stars   
42  Other 2724602275984 in 1 Precision Screwdriver...  4.2 out of 5 stars   
43  SAMSUNG Galaxy Tab S7 11-inch Android Tablet 1...  4.7 out of 5 stars   
44  Lenovo Smart Tab M10 Plus, FHD 10.3" Android T...  4.2 out of 5 stars   
45          2021 Apple iPad mini (Wi-Fi, 64GB) - Pink  4.1 out of 5 stars   
46  Samsung Galaxy Tab S7 FE 2021 Android Tablet 1...  4.5 out of 5 stars   
47  Atouch Tablet, Kids Tab A10,10.1 inch Tablet,D...                 NaN   
48  Samsung Electronics Galaxy Tab S7+ Wi-Fi, Myst...  4.7 out of 5 stars   
49  IPad AIR الجيل الرابع 10.9 حالة لوحة المفاتيح ...  5.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.6         54           

# Best Sellers in Computer Tablets (Page 2)

In [198]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966433031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [199]:
response = requests.get(url)
response.status_code

200

In [200]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [201]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [202]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [203]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'SAR 575.60'

In [204]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [205]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Atouch Tablet, Kids Tab A10,10.1 inch Tablet,Dual Sim,4GB Ram,64GB Rom,4G Lite With Gifts (Black)




SAR 342.77
342.77


In [206]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [207]:
products_df20 = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df20

pro_name            pro_rate  \
0   Atouch Tablet, Kids Tab A10,10.1 inch Tablet,D...                 NaN   
1   Lenovo Tab M10 HD (2nd Gen), X306F, 10.1"HD Ta...                 NaN   
2    2021 Apple 10.2-inch iPad (Wi-Fi, 64GB) - Silver  4.2 out of 5 stars   
3   Lenovo Tab M8 HD 2ND GEN (TB-8505F), 8 inch Ta...  3.8 out of 5 stars   
4   ATOUCH X10 7-Inch Tablet, Dual SIM, 32GB ROM,3...                 NaN   
5   5G WiFi 2 in 1 Tablet 10 inch Android 10.0 Tab...  3.0 out of 5 stars   
6   AOYODKG 2 in 1 Tablet 10.1 inch Android 10.0 T...  3.9 out of 5 stars   
7   2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
8   2021 Apple 10.2-inch iPad (Wi-Fi + Cellular, 2...  4.2 out of 5 stars   
9   C idea CM802 Android Tablet, 8Inch Tablet, 3gb...                 NaN   
10  2021 Apple iPad Pro (12.9-inch, Wi-Fi + Cellul...  4.9 out of 5 stars   
11  Microsoft Surface Pro 7 Tablet - 12.3 Inch, 10...  3.4 out of 5 stars   
12  5G Wi-Fi Tablet 10 Inch Android Tablets Octa C...  3.5 out of 5 stars   
13  Lenovo Tab M10 (TB-X505X), 10.1 Inch Tablet, 1...  3.8 out of 5 stars   
14  Xiaomi Pad 5 11" Tablet, 128GB, 6GB RAM, Wi-Fi...                 NaN   
15  Samsung Galaxy Tab S6 Lite, 64GB, 4GB RAM, Wi-...  4.3 out of 5 stars   
16  Pritom 7 inch Kids Tablet, Quad Core Android 1...  3.6 out of 5 stars   
17  2021 Apple iPad Pro (11-inch, Wi-Fi + Cellular...  4.6 out of 5 stars   
18  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
19  2021 Apple iPad Pro (11-inch, Wi-Fi + Cellular...  4.6 out of 5 stars   
20  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
21  2021 Apple iPad Pro (12.9-inch, Wi-Fi, 128GB) ...  4.9 out of 5 stars   
22  SAMSUNG Galaxy Tab S7+ Plus 12.4-inch Android ...  4.7 out of 5 stars   
23  10" Windows 10 FWIN232 PRO S2 Fusion5 Ultra Sl...  4.0 out of 5 stars   
24  Lenovo Tab M7 (TB-7305X) 7 inch Tablet, Wi-Fi ...  3.2 out of 5 stars   
25  2 in 1 Android 10.0 Tablet 10 Inch 5G WiFi Tab...  3.8 out of 5 stars   
26  Apple iPad Pro (12.9-inch, Wi-Fi, 256GB) - Silver  4.3 out of 5 stars   
27  2020 Apple iPad Air (10.9-inch, Wi-Fi, 256GB) ...  4.4 out of 5 stars   
28  C idea CM496, 7-inch Smart Android Tablet, Dua...                 NaN   
29  SAMSUNG Galaxy Tab S7 11-inch Android Tablet 1...  4.7 out of 5 stars   
30  Xiaomi Pad 5 11" Tablet, 256GB, 6GB RAM, Wi-Fi...  5.0 out of 5 stars   
31  HUAWEI MatePad T8 Tablet, 8 inch, 32GB 2GB RAM...                 NaN   
32  SAMSUNG Galaxy Tab S7 11-inch Android Tablet 1...  4.7 out of 5 stars   
33  Tablet 10.1 inch System 8.1 Tablet PC, 6GB RAM...                 NaN   
34  SAMSUNG Galaxy Tab S7 11-inch Android Tablet 1...  4.7 out of 5 stars   
35  Datazone Kids tablet, Childern tablet 7.0 inch...  1.0 out of 5 stars   
36  2021 Apple iPad Pro (11-inch, Wi-Fi, 256GB) - ...  4.6 out of 5 stars   
37  2021 Apple iPad Pro (12.9-inch, Wi-Fi, 256GB) ...  4.9 out of 5 stars   
38  2021 Apple iPad Pro (11-inch, Wi-Fi + Cellular...  4.6 out of 5 stars   
39  2021 Apple 10.2-inch iPad (Wi-Fi + Cellular, 2...  4.2 out of 5 stars   
40  Samsung Electronics Galaxy Tab S7 FE 2021 Andr...  4.5 out of 5 stars   
41  SAMSUNG Galaxy Tab S6, 10.5", 6G RAM, 128GB, L...  4.7 out of 5 stars   
42  Lenovo Tab M10 FHD Plus 2nd GEN (TB-X606X), 10...  3.8 out of 5 stars   
43  Lenovo M7 (TB-7305X) 7 Inch Tablet, Wi-Fi + Ce...  3.7 out of 5 stars   
44  2021 Apple iPad Pro (12.9-inch, Wi-Fi + Cellul...  4.9 out of 5 stars   
45  Lume Cube Broadcast Lighting Kit | Self Broadc...  4.4 out of 5 stars   
46  Slim Folio Pro for iPad Pro 11-inch (1st and 2...  4.0 out of 5 stars   
47  8" Windows Tablet with HDMI Port,1280x800 Touc...  2.5 out of 5 stars   
48  Lenovo Yoga Smart Tablet, 10.1" FHD (1920x1200...                 NaN   
49  Samsung Galaxy Tab Active3 Enterprise Edition ...  4.1 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             NaN        NaN           

In [216]:
df = pd.concat([products_df1,products_df2, products_df3, products_df4, products_df5, products_df6, products_df7, products_df8, 
             products_df9, products_df10, products_df11, products_df12, products_df13, products_df14, products_df15, 
             products_df16, products_df17, products_df18, products_df19, products_df20])

In [217]:
df

pro_name            pro_rate  \
0   SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB,...  3.0 out of 5 stars   
1   Samsung Galaxy A12 LTE Dual SIM Smartphone - 6...  1.0 out of 5 stars   
2                Apple 20W USB-C Power Adapter, White  4.5 out of 5 stars   
3   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.1 out of 5 stars   
4                    Apple AirPods with Charging Case  4.1 out of 5 stars   
..                                                ...                 ...   
45  Lume Cube Broadcast Lighting Kit | Self Broadc...  4.4 out of 5 stars   
46  Slim Folio Pro for iPad Pro 11-inch (1st and 2...  4.0 out of 5 stars   
47  8" Windows Tablet with HDMI Port,1280x800 Touc...  2.5 out of 5 stars   
48  Lenovo Yoga Smart Tablet, 10.1" FHD (1920x1200...                 NaN   
49  Samsung Galaxy Tab Active3 Enterprise Edition ...  4.1 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             3.0          2                2    SAR 539.00          539.00  
1             1.0          2                2    SAR 539.00          539.00  
2             4.5        359              359     SAR 79.00           79.00  
3             4.1         40               40    SAR 499.00          499.00  
4             4.1      2,777             2777    SAR 475.00          475.00  
..            ...        ...              ...           ...             ...  
45            4.4      1,044             1044    SAR 674.69          674.69  
46            4.0          1                1    SAR 505.22          505.22  
47            2.5          3                3    SAR 659.83          659.83  
48            NaN        NaN              NaN  SAR 1,026.26         1026.26  
49            4.1         10               10  SAR 2,638.63         2638.63  

[1000 rows x 7 columns]

In [257]:
df['i'] = y
y=[]
for i in range (0,1000):
    y.append(i) 

In [262]:
df =df.set_index(df['i'])

In [263]:
df

pro_name            pro_rate  \
i                                                                            
0    SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB,...  3.0 out of 5 stars   
1    Samsung Galaxy A12 LTE Dual SIM Smartphone - 6...  1.0 out of 5 stars   
2                 Apple 20W USB-C Power Adapter, White  4.5 out of 5 stars   
3    SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.1 out of 5 stars   
4                     Apple AirPods with Charging Case  4.1 out of 5 stars   
..                                                 ...                 ...   
995  Lume Cube Broadcast Lighting Kit | Self Broadc...  4.4 out of 5 stars   
996  Slim Folio Pro for iPad Pro 11-inch (1st and 2...  4.0 out of 5 stars   
997  8" Windows Tablet with HDMI Port,1280x800 Touc...  2.5 out of 5 stars   
998  Lenovo Yoga Smart Tablet, 10.1" FHD (1920x1200...                 NaN   
999  Samsung Galaxy Tab Active3 Enterprise Edition ...  4.1 out of 5 stars   

    pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  \
i                                                                              
0              3.0          2                2    SAR 539.00          539.00   
1              1.0          2                2    SAR 539.00          539.00   
2              4.5        359              359     SAR 79.00           79.00   
3              4.1         40               40    SAR 499.00          499.00   
4              4.1      2,777             2777    SAR 475.00          475.00   
..             ...        ...              ...           ...             ...   
995            4.4      1,044             1044    SAR 674.69          674.69   
996            4.0          1                1    SAR 505.22          505.22   
997            2.5          3                3    SAR 659.83          659.83   
998            NaN        NaN              NaN  SAR 1,026.26         1026.26   
999            4.1         10               10  SAR 2,638.63         2638.63   

       i  
i         
0      0  
1      1  
2      2  
3      3  
4      4  
..   ...  
995  995  
996  996  
997  997  
998  998  
999  999  

[1000 rows x 8 columns]